In [1]:
using Distributions
using Interpolations
using Distributed
using DataFrames
using Printf
using JLD
using CSV
using Dierckx
using Dates
# using PyPlot
# using Seaborn

main_path = "/home/artur/BondPricing"
module_path = string(main_path, "/", "Julia/modules/")
include(string(module_path, "/", "TestFunctions.jl"))
modls = ["ModelObj", "AnalyticFunctions", 
         "BondPrInterp", "EqFinDiff", 
         "Batch", "FullInfoEq", "JointEq"]
for modl in modls
    include(string(joinpath(module_path, modl), "/", modl, ".jl"))
end

ENV["LINES"] = 750

┌ Info: Recompiling stale cache file /home/artur/.julia/compiled/v1.1/Distributions/xILW0.ji for Distributions [31c24e10-a181-5473-b8eb-7969acd0382f]
└ @ Base loading.jl:1184
┌ Info: Recompiling stale cache file /home/artur/.julia/compiled/v1.1/JLD/l8ijy.ji for JLD [4138dd39-2aa7-5051-a626-17a0bb65d9c8]
└ @ Base loading.jl:1184
┌ Info: Recompiling stale cache file /home/artur/.julia/compiled/v1.1/CSV/HHBkp.ji for CSV [336ed68f-0bac-5ca0-87d4-7b16caf5d00b]
└ @ Base loading.jl:1184
┌ Info: Recompiling stale cache file /home/artur/.julia/compiled/v1.1/AnalyticFunctions.ji for AnalyticFunctions [top-level]
└ @ Base loading.jl:1184
┌ Info: Recompiling stale cache file /home/artur/.julia/compiled/v1.1/BondPrInterp.ji for BondPrInterp [top-level]
└ @ Base loading.jl:1184
┌ Info: Recompiling stale cache file /home/artur/.julia/compiled/v1.1/EqFinDiff.ji for EqFinDiff [top-level]
└ @ Base loading.jl:1184
┌ Info: Recompiling stale cache file /home/artur/.julia/compiled/v1.1/DSP/OtML7.ji for DSP 

750

In [50]:
modls = ["ModelObj", "AnalyticFunctions", 
         "BondPrInterp", "EqFinDiff", 
         "Batch", "FullInfoEq", "JointEq"]
for modl in modls
    include(string(joinpath(module_path, modl), "/", modl, ".jl"))
end

In [56]:
mu_s = .5
kep = 25 * 10^-4
kotc = 50 * 10^-4
s_iota = 1e-4
r_iota = 0.0
r_lambda = .2
r_sigmah = .25
ep_m = 1.
ep_c = 3.
ep_p = 35.
otc_m = 1.

jep = JointEq.store_joint_eq_parameters(mu_s, kep, kotc;
                                        s_iota=s_iota,
                                        r_iota=r_iota,
                                        r_lambda=r_lambda,
                                        r_sigmah=r_sigmah)

# Check for missing parameters
# Lambda and sigmah can be NaN => CVM model
missing = false
if any([isnan(getfield(jep, x)) for x in [:mu_s, :kep, :kotc]])
    println("Missing Market Parameters!")
    missing = true
end
if any([isnan(getfield(jep.sfp, :iota)) for x in fieldnames(JointEq.FirmSpecificParams)])
    println("Missing Safe Firm's specific parameters!")
    missing = true
end
if any([isnan(getfield(jep.rfp, :iota)) for x in fieldnames(JointEq.FirmSpecificParams)])
    println("Missing Risky Firm's specific parameters!")
    missing = true
end

# #################################################################
# Safe and Risky Firms' Models ####################################
# #################################################################
cbt = Batch.get_bt(;comb_num=1, model="cvm")
sbt = Batch.get_bt(;comb_num=1, model="svm")

# Identify Firm Model
sf_model = .&(!isnan(jep.sfp.iota),!isnan(jep.sfp.lambda)) ? "svm" : "cvm"
rf_model = .&(!isnan(jep.rfp.iota),!isnan(jep.rfp.lambda)) ? "svm" : "cvm"

# Set Models
sf_bt = sf_model == "cvm" ? cbt : sbt
rf_bt = rf_model == "cvm" ? cbt : sbt
# #################################################################   

jeq= JointEq.ep_constructor(jep, sf_bt, rf_bt;
                        ep_m=ep_m,
                        ep_c=ep_c,
                        ep_p=ep_p,
                        run_pool_eq=false,
                        run_sep_eq=false,                       
                        sf_obj_fun=:firm_value,
                        rf_obj_fun=:MBR,
                        rerun_full_info=true,
                        rerun_misrep=true,
                        rerun_pool=false,
                        rerun_sep=false)

Setting parameter dictionary using unique combination ID...
Setting parameter dictionary using unique combination ID...
Setting parameter dictionary to batch object's parameter dictionary
Setting parameter values... 
Setting parameter dictionary using unique combination ID...
Setting initial vbl value to NaN
Setting initial vbh value to NaN
Setting initial c value to NaN
Setting initial p value to NaN
Constant Volatility Model: setting vbh to vbl, lambda to NaN
Setting parameter dictionary to batch object's parameter dictionary
Setting parameter values... 
Setting parameter dictionary using unique combination ID...
Loading SVM object...
Batch object file not found.
Batch Object is incompatible! Loading surfaces only instead.
Setting initial vbl value to NaN
Setting initial vbh value to NaN
Setting initial c value to NaN
Setting initial p value to NaN
Interpolating Bond Pricing Surfaces...
  0.207441 seconds (811.42 k allocations: 137.112 MiB, 9.71% gc time)
Batch object exists: true
In

Computing equity values... 
V0: 100.0; equity: 17.153232497389723
Equity Core Function Computation Time: 0.04487299919128418
Total Equity FD Core Function Computation Time: 0.200286865234375
Total computation time: 0.20599818229675293
Computing Equity Vmax
Vmax: 125.0
phi0: -64.0360777361995
phi1: 0.9949999999999999
pv_rfdebt: 86.2536364187513
debt_abs_per_diff: NaN
eq_abs_per_diff: NaN
Equity Vmax: 131.25
 
eq_max: 58.94943935035103
eq_vbl: 0.0
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 8.923001255309016
Equity Core Function Computation Time: 0.040370941162109375
Total Equity FD Core Function Computation Time: 0.08994507789611816
Total computation time: 0.09560799598693848
Computing Equity Vmax
Vmax: 125.0
phi0: -67.2250452521036
phi1: 0.9949999999999999
pv_rfdebt: 90.54902824148483
debt_abs_per_diff: NaN
eq_abs_per_diff: NaN
Equity Vmax: 131.25
 
eq_max: 52.95920800107071
eq_vbl: 0.0
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100

Computing equity values... 
V0: 100.0; equity: 86.78567401264381
Equity Core Function Computation Time: 0.04113507270812988
Total Equity FD Core Function Computation Time: 0.08902120590209961
Total computation time: 0.11069583892822266
Computing Equity Vmax
Vmax: 125.0
phi0: -13.012597481734112
phi1: 0.9999999999999998
pv_rfdebt: 17.527367255014916
debt_abs_per_diff: 0.0005605785217429761
eq_abs_per_diff: 0.000338309868025438
Equity Vmax: 213.7924197645393
 
eq_max: 200.77980902412108
eq_vbl: 0.0
Computing Constant Volatility Equity Values
Finished computing Constant Volatility Equity Values
Time to compute Constant Volatility Equity Values: 0.008121967315673828
 
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 86.78566835476465
Equity Core Function Computation Time: 0.04645180702209473
Total Equity FD Core Function Computation Time: 0.09988594055175781
Total computation time: 0.12145686149597168
Computing Equity Vmax
Vmax: 125.0
phi0: -13.012597481734112


Computing equity values... 
V0: 100.0; equity: 80.12978233281548
Equity Core Function Computation Time: 0.0684659481048584
Total Equity FD Core Function Computation Time: 0.12139415740966797
Total computation time: 0.14593100547790527
Computing Equity Vmax
Vmax: 125.0
phi0: -19.17645944676606
phi1: 0.9999999999999998
pv_rfdebt: 25.829804375811452
debt_abs_per_diff: 6.243631213931801e-5
eq_abs_per_diff: 0.000856451865232897
Equity Vmax: 235.70614279040458
 
eq_max: 216.5295840375969
eq_vbl: 0.0
Computing Constant Volatility Equity Values
Finished computing Constant Volatility Equity Values
Time to compute Constant Volatility Equity Values: 0.008226156234741211
 
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 80.12585539791263
Equity Core Function Computation Time: 0.046280860900878906
Total Equity FD Core Function Computation Time: 0.20063996315002441
Total computation time: 0.22492599487304688
Computing Equity Vmax
Vmax: 125.0
phi0: -19.17645944676606
phi

Computing equity values... 
V0: 100.0; equity: 72.97125671741043
Equity Core Function Computation Time: 0.06096291542053223
Total Equity FD Core Function Computation Time: 0.11309218406677246
Total computation time: 0.14379477500915527
Computing Equity Vmax
Vmax: 125.0
phi0: -25.340321411798005
phi1: 0.9999999999999998
pv_rfdebt: 34.132241496607996
debt_abs_per_diff: 5.27596080502767e-7
eq_abs_per_diff: 0.0009577266304370098
Equity Vmax: 300.8274042113857
 
eq_max: 275.486923357585
eq_vbl: 0.0
Computing Constant Volatility Equity Values
Finished computing Constant Volatility Equity Values
Time to compute Constant Volatility Equity Values: 0.008197784423828125
 
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 72.95167550641028
Equity Core Function Computation Time: 0.04665994644165039
Total Equity FD Core Function Computation Time: 0.2012012004852295
Total computation time: 0.23357915878295898
Computing Equity Vmax
Vmax: 125.0
phi0: -25.340321411798005
phi1

...

debt_abs_per_diff: 1.540224141605867e-7
eq_abs_per_diff: 0.0008750052848319692
Equity Vmax: 514.5169494226984
 
eq_max: 472.3768253164815
eq_vbl: 0.0
Computing Constant Volatility Equity Values
Finished computing Constant Volatility Equity Values
Time to compute Constant Volatility Equity Values: 0.008091926574707031
 
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 66.88508198572214; equity: 2.5109958278392703
Equity Core Function Computation Time: 0.037420034408569336
Total Equity FD Core Function Computation Time: 0.07675504684448242
Total computation time: 0.2339768409729004
eq_vbl: 2.5109958278392703
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 53.0591851941312
Equity Core Function Computation Time: 0.04222702980041504
Total Equity FD Core Function Computation Time: 0.0766611099243164
Computing Constant Volatility Equity Values
Finished computing Constant Volatility Equity Values
Time to compute Constant Volatility Equity Values: 0.0

Computing equity values... 
V0: 100.0; equity: 50.00786039698639
Equity Core Function Computation Time: 0.04281187057495117
Total Equity FD Core Function Computation Time: 0.08492207527160645
Total computation time: 0.3221778869628906
Computing Equity Vmax
Vmax: 125.0
phi0: -42.139897575397896
phi1: 0.9949999999999999
pv_rfdebt: 56.760493969746804
debt_abs_per_diff: NaN
eq_abs_per_diff: NaN
Vmax: 125.0
phi0: -42.139897575397896
phi1: 0.9999999999999998
pv_rfdebt: 56.760493969746804
debt_abs_per_diff: 1.540224141605867e-7
eq_abs_per_diff: 0.0008750052848319692
Equity Vmax: 514.5169494226984
 
eq_max: 2.2232236406371673
eq_vbl: 0.0
eq_vbl: 0.0
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 55.98107072609833
Equity Core Function Computation Time: 0.06406998634338379
Total Equity FD Core Function Computation Time: 0.09947776794433594
Computing Constant Volatility Equity Values
Finished computing Constant Volatility Equity Values
Time to compute Constant Volat

Excessive output truncated after 524293 bytes.

V0: 100.0; equity: 49.69829493745001
Equity Core Function Computation Time: 0.037837982177734375
Total Equity FD Core Function Computation Time: 0.0799109935760498
Total computation time: 0.4234499931335449
Computing Equity Vmax
Vmax: 125.0
phi0: -42.139897575397896
phi1: 0.9949999999999999
pv_rfdebt: 56.760493969746804
debt_abs_per_diff: NaN
eq_abs_per_diff: NaN
Vmax: 125.0
phi0: -42.139897575397896
phi1: 0.9999999999999998
pv_rfdebt: 56.760493969746804
debt_abs_per_diff: 1.540224141605867e-7
eq_abs_per_diff: 0.0008750052848319692
Equity Vmax: 514.5169494226984
 


Main.JointEq.EPStruct(Main.JointEq.JointFirms(Main.JointEq.JointKStruct(0.5, 1.245075176429021, 1.0, 3.0, 35.0, 48.43065326479742, NaN, NaN, NaN, NaN), ModelObj.Firm
  mu_b: Float64 1.0
  m: Float64 1.0
  c: Float64 NaN
  p: Float64 NaN
  vbl: Float64 NaN
  vbh: Float64 NaN
  pm: ModelObj.FirmParams
  model: String "cvm"
  bi: ModelObj.BPrInputs
  bs: ModelObj.BPrSurfs
  bf: ModelObj.BPrInterpFuns
  bit: ModelObj.BPrFixedTTMInputs
  bft: ModelObj.BPrInterpFuns
  optKS: ModelObj.KStruct
, ModelObj.Firm
  mu_b: Float64 1.0
  m: Float64 1.0
  c: Float64 NaN
  p: Float64 NaN
  vbl: Float64 NaN
  vbh: Float64 NaN
  pm: ModelObj.FirmParams
  model: String "svm"
  bi: ModelObj.BPrInputs
  bs: ModelObj.BPrSurfs
  bf: ModelObj.BPrInterpFuns
  bit: ModelObj.BPrFixedTTMInputs
  bft: ModelObj.BPrInterpFuns
  optKS: ModelObj.KStruct
, Batch.BatchStruct
  model: String "cvm"
  dfn: Batch.DirFileNames
  dfc: Batch.BatchDFColumns
  mi: Batch.ModelInputs
  bp: Batch.BatchParams
  coupon_grid: Array{Flo

In [59]:
jeq.rfdf

1×27 DataFrame. Omitted printing of 20 columns
│ Row │ MBR     │ V0      │ alpha   │ c       │ debt    │ delta   │ eq_deriv   │
│     │ Float64 │ Float64 │ Float64 │ Float64 │ Float64 │ Float64 │ Float64    │
├─────┼─────────┼─────────┼─────────┼─────────┼─────────┼─────────┼────────────┤
│ 1   │ 13.2612 │ 100.0   │ 0.6     │ 3.0     │ 43.6458 │ 0.02    │ 2.21491e-5 │

In [58]:
jeq.misrep

1×48 DataFrame. Omitted printing of 42 columns
│ Row │ sf_defaults_first │ kappa   │ mu_s    │ m       │ c       │ p       │
│     │ Bool              │ Float64 │ Float64 │ Float64 │ Float64 │ Float64 │
├─────┼───────────────────┼─────────┼─────────┼─────────┼─────────┼─────────┤
│ 1   │ false             │ 0.0025  │ 1.0     │ 1.0     │ 3.0     │ 35.0    │

In [52]:
# Measure of Firms and Standardized Bond
ep_jks = JointEq.store_ep_params(jep.mu_s;
                         ep_m=ep_m,
                         ep_c=ep_c,
                         ep_p=ep_p)

# Measure of Firms and Standardized Bond
ep_jks = JointEq.store_ep_params(jep.mu_s;
                                 ep_m=ep_m,
                                 ep_c=ep_c,
                                 ep_p=ep_p)

# Check for missing parameters
if any([isnan(getfield(ep_jks, x)) for x in [:mu_s, :m, :c, :p]])
    println("Missing Electronic Platform parameters")
    return
end

# epst = JointEq.ep_constructor(jep, sf_bt, rf_bt; ep_jks=ep_jks,
#                                 rerun_full_info=false,
#                                 rerun_misrep=true,
#                                 rerun_pool=false,    
#                                 rerun_sep=false)

# Adjust parameter dictionaries
for var in [:alpha, :pi, :r, :gross_delta, :xi, :sigmal]
    sf_bt.mi._svm_dict[var] = getfield(jep.fcp, var)
    rf_bt.mi._svm_dict[var] = getfield(jep.fcp, var)
end

# Form EP Safe Firm
ep_sf_comb_num = Batch.get_batch_comb_num(sf_bt;
                                          iota=jep.sfp.iota,
                                          kappa=jep.kep,
                                          lambda=jep.sfp.lambda,
                                          sigmah=jep.sfp.sigmah)[1, :comb_num]
_, ep_sf_svm = Batch.get_bt_mobj(;model=sf_bt.model, comb_num=ep_sf_comb_num)

# Form EP Risky Firm
ep_rf_comb_num = Batch.get_batch_comb_num(rf_bt;
                                    iota=jep.rfp.iota,
                                    kappa=jep.kep,
                                    lambda=jep.rfp.lambda,
                                    sigmah=jep.rfp.sigmah)[1, :comb_num]
_, ep_rf_svm = Batch.get_bt_mobj(;model=rf_bt.model, comb_num=ep_rf_comb_num)

# Joint Firm Constructor ##########################################
ep_jf = JointEq.joint_firm_constructor(ep_sf_svm, ep_rf_svm;
                               jks=ep_jks,
                               load_results_dfs=false)
# #################################################################

# Path to Results Directory
ep_ks_path = JointEq.get_ep_results_path(ep_jf; ep_dir=JointEq.ep_dir)

Setting parameter dictionary to batch object's parameter dictionary
Setting parameter values... 
Setting parameter dictionary using unique combination ID...
Setting initial vbl value to NaN
Setting initial vbh value to NaN
Setting initial c value to NaN
Setting initial p value to NaN
Constant Volatility Model: setting vbh to vbl, lambda to NaN
Setting parameter dictionary to batch object's parameter dictionary
Setting parameter values... 
Setting parameter dictionary using unique combination ID...
Loading SVM object...
Batch object file not found.
Batch Object is incompatible! Loading surfaces only instead.
Setting initial vbl value to NaN
Setting initial vbh value to NaN
Setting initial c value to NaN
Setting initial p value to NaN
Interpolating Bond Pricing Surfaces...
  0.199644 seconds (811.43 k allocations: 137.114 MiB, 11.62% gc time)
Batch object exists: true
Interpolating bond pricing surfaces...
  0.191416 seconds (811.42 k allocations: 137.112 MiB, 7.98% gc time)


"/mnt/ide0/home/artur/BondPricing/Julia/Results/EP/m_1.00__c_3.000__p_35.000"

In [53]:
rf_bt.mi.comb_res_path


"/mnt/ide0/home/artur/BondPricing/Julia/Results/SVM/m_1.00/mub_1.00__xi_1.00__kappa_10.00_bp__gross_delta_200.00_bp__iota_0.00_bp__lambda_0.100__sigmal_0.150__sigmah_0.200"

In [18]:

#     # Form EP Risky Firm
#     ep_rf_comb_num = get_batch_comb_num(rf_bt;
#                                         iota=jep.rfp.iota,
#                                         kappa=jep.kep,
#                                         lambda=jep.rfp.lambda,
#                                         sigmah=jep.rfp.sigmah)[1, :comb_num]
#     _, ep_rf_svm = get_bt_mobj(;model=rf_bt.model, comb_num=ep_rf_comb_num)
    




Setting parameter dictionary to batch object's parameter dictionary
Setting parameter values... 


9

# CVM adn SVM Diagnostics and Compilation

In [ ]:
# Set m=1. and model = "cvm"
plot_script_path = string(main_path, "/Julia/Batch/")
plot_script_name = "diag_compilation.jl"
cvm_res = include(string(plot_script_path, "/", plot_script_name))

In [ ]:
mu_s = .5
kep = 25 * 10^-4
kotc = 50 * 10^-4
s_iota = 1e-4
r_iota = 0.0
r_lambda = .2
r_sigmah = .25
ep_m = 1.
ep_c = 3.
ep_p = 35.
otc_m = 1.

jep = JointEq.store_joint_eq_parameters(mu_s, kep, kotc;
                                    s_iota=s_iota,
                                    r_iota=r_iota,
                                    r_lambda=r_lambda,
                                    r_sigmah=r_sigmah)


jeq = JointEq.ep_otc_constructor(jep.mu_s, jep.kep, jep.kotc;
                                 jep=deepcopy(jep),
                                 sf_obj_fun=:firm_value,
                                 rf_obj_fun=:MBR,
                                 run_pool_eq=false,
                                 run_sep_eq=false,                                              
                                 s_iota=s_iota,
                                 s_lambda=NaN,
                                 s_sigmah=NaN,
                                 r_iota=r_iota,
                                 r_lambda=r_lambda,
                                 r_sigmah=r_sigmah,
                                 ep_m=ep_m,
                                 ep_c=ep_c,
                                 ep_p=ep_p,
                                 otc_m=otc_m)


# # #################################################################
# # Safe and Risky Firms' Models ####################################
# # #################################################################
# cbt = Batch.get_bt(;comb_num=1, model="cvm")
# sbt = Batch.get_bt(;comb_num=1, model="svm")

# # Identify Firm Model
# sf_model = .&(!isnan(jep.sfp.iota),!isnan(jep.sfp.lambda)) ? "svm" : "cvm"
# rf_model = .&(!isnan(jep.rfp.iota),!isnan(jep.rfp.lambda)) ? "svm" : "cvm"

# # Set Models
# sf_bt = sf_model == "cvm" ? cbt : sbt
# rf_bt = rf_model == "cvm" ? cbt : sbt

Setting parameter dictionary using unique combination ID...
Setting parameter dictionary using unique combination ID...
Setting parameter dictionary to batch object's parameter dictionary
Setting parameter values... 
Setting parameter dictionary using unique combination ID...
Setting initial vbl value to NaN
Setting initial vbh value to NaN
Setting initial c value to NaN
Setting initial p value to NaN
Constant Volatility Model: setting vbh to vbl, lambda to NaN
Setting parameter dictionary to batch object's parameter dictionary
Setting parameter values... 
Setting parameter dictionary using unique combination ID...
Batch object exists: false
Setting initial vbl value to NaN
Setting initial vbh value to NaN
Setting initial c value to NaN
Setting initial p value to NaN


In [ ]:
jeq

In [88]:
epst.jf.jks = ep_jks

Main.JointEq.JointKStruct(0.5, 1.245075176429021, 1.0, 3.0, 35.0, 48.4306532304087, NaN, NaN, NaN, NaN)

In [47]:
# Measure of Firms and Standardized Bond
ep_jks = JointEq.store_ep_params(jep.mu_s;
                         ep_m=ep_m,
                         ep_c=ep_c,
                         ep_p=ep_p)

epst = JointEq.ep_constructor(jep, sf_bt, rf_bt; ep_jks=ep_jks)

Setting parameter dictionary to batch object's parameter dictionary
Setting parameter values... 
Setting parameter dictionary using unique combination ID...
Setting initial vbl value to NaN
Setting initial vbh value to NaN
Setting initial c value to NaN
Setting initial p value to NaN
Constant Volatility Model: setting vbh to vbl, lambda to NaN
Setting parameter dictionary to batch object's parameter dictionary
Setting parameter values... 
Setting parameter dictionary using unique combination ID...
Batch object exists: true
Loading SVM object...
Unable to load batch object file.
Batch Object is incompatible! Loading surfaces only instead.
Setting initial vbl value to NaN
Setting initial vbh value to NaN
Setting initial c value to NaN
Setting initial p value to NaN
Interpolating Bond Pricing Surfaces...
  0.206323 seconds (811.42 k allocations: 137.112 MiB, 12.96% gc time)
Interpolating bond pricing surfaces...
  0.180434 seconds (811.43 k allocations: 137.113 MiB, 6.05% gc time)
COUNT: 

Computing equity values... 
V0: 100.0; equity: 8.923001255309016
Equity Core Function Computation Time: 0.0555109977722168
Total Equity FD Core Function Computation Time: 0.08815598487854004
Total computation time: 0.09385204315185547
Computing Equity Vmax
Vmax: 125.0
phi0: -67.2250452521036
phi1: 0.9949999999999999
pv_rfdebt: 90.54902824148483
debt_abs_per_diff: NaN
eq_abs_per_diff: NaN
Equity Vmax: 131.25
 
eq_max: 52.95920800107071
eq_vbl: 0.0
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 2.419508354041986
Equity Core Function Computation Time: 0.032652854919433594
Total Equity FD Core Function Computation Time: 0.17330002784729004
Total computation time: 0.17897391319274902
Computing Equity Vmax
Vmax: 125.0
phi0: -70.4140127680077
phi1: 0.9949999999999999
pv_rfdebt: 94.84442006421837
debt_abs_per_diff: NaN
eq_abs_per_diff: NaN
Equity Vmax: 131.25
 
eq_max: 46.2443741920456
eq_vbl: 0.0
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100

debt_abs_per_diff: 0.0005605785217429761
eq_abs_per_diff: 0.000338309868025438
Equity Vmax: 213.7924197645393
 
eq_max: 200.77980902412108
eq_vbl: 0.0
Computing Constant Volatility Equity Values
Finished computing Constant Volatility Equity Values
Time to compute Constant Volatility Equity Values: 0.008118867874145508
 
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 86.78566835476465
Equity Core Function Computation Time: 0.05525016784667969
Total Equity FD Core Function Computation Time: 0.09585785865783691
Total computation time: 0.11760997772216797
Computing Equity Vmax
Vmax: 125.0
phi0: -13.012597481734112
phi1: 0.9999999999999998
pv_rfdebt: 17.527367255014916
debt_abs_per_diff: 0.0005605785217429761
eq_abs_per_diff: 0.000338309868025438
Equity Vmax: 213.7924197645393
 
eq_max: 200.77980902412108
eq_vbl: 0.0
Computing Constant Volatility Equity Values
Finished computing Constant Volatility Equity Values
Time to compute Constant Volatility Equity Value

Computing equity values... 
V0: 100.0; equity: 80.12585541238255
Equity Core Function Computation Time: 0.03271603584289551
Total Equity FD Core Function Computation Time: 0.1803891658782959
Total computation time: 0.20469999313354492
Computing Equity Vmax
Vmax: 125.0
phi0: -19.17645944676606
phi1: 0.9999999999999998
pv_rfdebt: 25.829804375811452
debt_abs_per_diff: 6.243631213931801e-5
eq_abs_per_diff: 0.000856451865232897
Equity Vmax: 235.70614279040458
 
eq_max: 216.5295840375969
eq_vbl: 0.0
Computing Constant Volatility Equity Values
Finished computing Constant Volatility Equity Values
Time to compute Constant Volatility Equity Values: 0.008085966110229492
 
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 80.12084296406083
Equity Core Function Computation Time: 0.03537487983703613
Total Equity FD Core Function Computation Time: 0.07605695724487305
Total computation time: 0.1003730297088623
Computing Equity Vmax
Vmax: 125.0
phi0: -19.17645944676606
phi1:

Computing equity values... 
V0: 100.0; equity: 72.95167557165438
Equity Core Function Computation Time: 0.03282284736633301
Total Equity FD Core Function Computation Time: 0.18164992332458496
Total computation time: 0.2127549648284912
Computing Equity Vmax
Vmax: 125.0
phi0: -25.340321411798005
phi1: 0.9999999999999998
pv_rfdebt: 34.132241496607996
debt_abs_per_diff: 5.27596080502767e-7
eq_abs_per_diff: 0.0009577266304370098
Equity Vmax: 300.8274042113857
 
eq_max: 275.486923357585
eq_vbl: 0.0
Computing Constant Volatility Equity Values
Finished computing Constant Volatility Equity Values
Time to compute Constant Volatility Equity Values: 0.008038997650146484
 
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 72.92589737676947
Equity Core Function Computation Time: 0.03535008430480957
Total Equity FD Core Function Computation Time: 0.07640504837036133
Total computation time: 0.10756993293762207
Computing Equity Vmax
Vmax: 125.0
phi0: -25.340321411798005
phi1

...

debt_abs_per_diff: 1.540224141605867e-7
eq_abs_per_diff: 0.0008750052848319692
Equity Vmax: 514.5169494226984
 
eq_max: 472.3768253164815
eq_vbl: 0.0
Computing Constant Volatility Equity Values
Finished computing Constant Volatility Equity Values
Time to compute Constant Volatility Equity Values: 0.008092164993286133
 
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 66.88508194462356; equity: 2.5109958440715388
Equity Core Function Computation Time: 0.032340049743652344
Total Equity FD Core Function Computation Time: 0.07243704795837402
Total computation time: 0.22837400436401367
eq_vbl: 2.5109958440715388
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 53.059185210621884
Equity Core Function Computation Time: 0.03220796585083008
Total Equity FD Core Function Computation Time: 0.06708312034606934
Computing Constant Volatility Equity Values
Finished computing Constant Volatility Equity Values
Time to compute Constant Volatility Equity Values:

Computing equity values... 
V0: 100.0; equity: 56.09925256782496
Equity Core Function Computation Time: 0.03238105773925781
Total Equity FD Core Function Computation Time: 0.06429719924926758
Computing Constant Volatility Equity Values
Finished computing Constant Volatility Equity Values
Time to compute Constant Volatility Equity Values: 0.008068084716796875
 
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 50.00786039710713
Equity Core Function Computation Time: 0.032321929931640625
Total Equity FD Core Function Computation Time: 0.07448315620422363
Total computation time: 0.19890284538269043
Computing Equity Vmax
Vmax: 125.0
phi0: -42.139897575397896
phi1: 0.9949999999999999
pv_rfdebt: 56.760493969746804
debt_abs_per_diff: NaN
eq_abs_per_diff: NaN
Vmax: 125.0
phi0: -42.139897575397896
phi1: 0.9999999999999998
pv_rfdebt: 56.760493969746804
debt_abs_per_diff: 1.540224141605867e-7
eq_abs_per_diff: 0.0008750052848319692
Equity Vmax: 514.5169494226984
 
eq_ma

Excessive output truncated after 524307 bytes.

V0: 100.0; equity: 49.698294937269914
Equity Core Function Computation Time: 0.03293299674987793
Total Equity FD Core Function Computation Time: 0.0750889778137207
Total computation time: 0.39681220054626465
Computing Equity Vmax
Vmax: 125.0
phi0: -42.139897575397896
phi1: 0.9949999999999999
pv_rfdebt: 56.760493969746804
debt_abs_per_diff: NaN
eq_abs_per_diff: NaN
Vmax: 125.0
phi0: -42.139897575397896
phi1: 0.9999999999999998
pv_rfdebt: 56.760493969746804
debt_abs_per_diff: 1.540224141605867e-7
eq_abs_per_diff: 0.0008750052848319692
Equity Vmax: 514.5169494226984
 
eq_max: 2.127559115375444
Computing Equity Vmax
Vmax: 125.0
phi0: -42.139897575397896
phi1: 0.9949999999999999
pv_rfdebt: 56.760493969746804


Main.JointEq.EPStruct(Main.JointEq.JointFirms(Main.JointEq.JointKStruct(NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN), ModelObj.Firm
  mu_b: Float64 1.0
  m: Float64 1.0
  c: Float64 NaN
  p: Float64 NaN
  vbl: Float64 NaN
  vbh: Float64 NaN
  pm: ModelObj.FirmParams
  model: String "cvm"
  bi: ModelObj.BPrInputs
  bs: ModelObj.BPrSurfs
  bf: ModelObj.BPrInterpFuns
  bit: ModelObj.BPrFixedTTMInputs
  bft: ModelObj.BPrInterpFuns
  optKS: ModelObj.KStruct
, ModelObj.Firm
  mu_b: Float64 1.0
  m: Float64 1.0
  c: Float64 NaN
  p: Float64 NaN
  vbl: Float64 NaN
  vbh: Float64 NaN
  pm: ModelObj.FirmParams
  model: String "svm"
  bi: ModelObj.BPrInputs
  bs: ModelObj.BPrSurfs
  bf: ModelObj.BPrInterpFuns
  bit: ModelObj.BPrFixedTTMInputs
  bft: ModelObj.BPrInterpFuns
  optKS: ModelObj.KStruct
, Batch.BatchStruct
  model: String "cvm"
  dfn: Batch.DirFileNames
  dfc: Batch.BatchDFColumns
  mi: Batch.ModelInputs
  bp: Batch.BatchParams
  coupon_grid: Array{Float64}((26,)) [0.25, 0.5, 1.0,

In [137]:
epst.sfdf

1×27 DataFrame. Omitted printing of 21 columns
│ Row │ ROE     │ V0      │ alpha   │ c       │ debt    │ delta   │
│     │ Float64 │ Float64 │ Float64 │ Float64 │ Float64 │ Float64 │
├─────┼─────────┼─────────┼─────────┼─────────┼─────────┼─────────┤
│ 1   │ 27.5335 │ 100.0   │ 0.6     │ 3.0     │ 56.76   │ 0.0199  │

In [51]:
epst.rfdf

1×27 DataFrame. Omitted printing of 20 columns
│ Row │ ROE     │ V0      │ alpha   │ c       │ debt    │ delta   │ eq_deriv   │
│     │ Float64 │ Float64 │ Float64 │ Float64 │ Float64 │ Float64 │ Float64    │
├─────┼─────────┼─────────┼─────────┼─────────┼─────────┼─────────┼────────────┤
│ 1   │ 13.2612 │ 100.0   │ 0.6     │ 3.0     │ 43.6458 │ 0.02    │ 2.21491e-5 │

In [49]:
epst.pool

2×32 DataFrame. Omitted printing of 27 columns
│ Row │ sf_defaults_first │ fi_vb   │ sf_vb   │ rf_vb   │ vb      │
│     │ Bool              │ Float64 │ Float64 │ Float64 │ Float64 │
├─────┼───────────────────┼─────────┼─────────┼─────────┼─────────┤
│ 1   │ false             │ 58.5313 │ 58.5313 │ NaN     │ 60.019  │
│ 2   │ false             │ 61.3236 │ NaN     │ 60.019  │ 60.019  │

In [52]:
epst.misrep

2×32 DataFrame. Omitted printing of 26 columns
│ Row │ sf_defaults_first │ fi_vb   │ sf_vb   │ rf_vb   │ vb      │ eq_deriv   │
│     │ Bool              │ Float64 │ Float64 │ Float64 │ Float64 │ Float64    │
├─────┼───────────────────┼─────────┼─────────┼─────────┼─────────┼────────────┤
│ 1   │ false             │ 60.1152 │ 60.1152 │ NaN     │ 61.3286 │ 0.589506   │
│ 2   │ false             │ 62.9833 │ NaN     │ 61.3286 │ 61.3286 │ -0.0005546 │

In [53]:
epst.sep

2×32 DataFrame. Omitted printing of 27 columns
│ Row │ sf_defaults_first │ fi_vb   │ sf_vb   │ rf_vb   │ vb      │
│     │ Bool              │ Float64 │ Float64 │ Float64 │ Float64 │
├─────┼───────────────────┼─────────┼─────────┼─────────┼─────────┤
│ 1   │ false             │ 65.9808 │ 65.9808 │ NaN     │ 67.6609 │
│ 2   │ false             │ 69.1287 │ NaN     │ 67.6609 │ 67.6609 │

In [98]:
ep_ks_path = JointEq.get_ep_results_path(epst.jf)

"/mnt/ide0/home/artur/BondPricing/Julia/Results/EP/m_1.0__c_3.00__p_35.00"

In [100]:
ep_ks_fi_path = JointEq.get_ep_full_info_path(epst)

"/mnt/ide0/home/artur/BondPricing/Julia/Results/EP/m_1.0__c_3.00__p_35.00/FI"

In [184]:
CSV.write(string(ep_ks_fi_path, "/", dfname, ".csv"), vcat(epst.sfdf, epst.rfdf))

"/mnt/ide0/home/artur/BondPricing/Julia/Results/EP/m_1.0__c_3.00__p_35.00/FI/fidf.csv"

In [191]:
fidf =vcat(epst.sfdf, epst.rfdf)

2×27 DataFrame. Omitted printing of 21 columns
│ Row │ ROE     │ V0      │ alpha   │ c       │ debt    │ delta   │
│     │ Float64 │ Float64 │ Float64 │ Float64 │ Float64 │ Float64 │
├─────┼─────────┼─────────┼─────────┼─────────┼─────────┼─────────┤
│ 1   │ 27.5335 │ 100.0   │ 0.6     │ 3.0     │ 56.76   │ 0.0199  │
│ 2   │ 13.2612 │ 100.0   │ 0.6     │ 3.0     │ 43.6458 │ 0.02    │

In [201]:
CSV.write(string(ep_ks_fi_path, "/", dfname, ".csv"), vcat(epst.sfdf, epst.rfdf))

"/mnt/ide0/home/artur/BondPricing/Julia/Results/EPm_1.0__c_3.00__p_35.00/FI/fidf.csv"

In [537]:
fidf_name = "fidf"
ep_ks_path = JointEq.get_ep_results_path(epst.jf)
fidf_col_types = vcat(fill(Float64, 9), [Bool], fill(Float64, 17))
if !JointEq.exists_ep_df(epst.jf, fidf_name)
    CSV.write(string(ep_ks_path, "/", fidf_name, ".csv"), vcat(epst.sfdf, epst.rfdf))
else
    fidf = CSV.read(string(ep_ks_path, "/", fidf_name, ".csv"); types=dfcols) 
end

2×27 DataFrame. Omitted printing of 21 columns
│ Row │ ROE     │ V0      │ alpha   │ c       │ debt    │ delta   │
│     │ Float64 │ Float64 │ Float64 │ Float64 │ Float64 │ Float64 │
├─────┼─────────┼─────────┼─────────┼─────────┼─────────┼─────────┤
│ 1   │ 27.5335 │ 100.0   │ 0.6     │ 3.0     │ 56.76   │ 0.0199  │
│ 2   │ 13.2612 │ 100.0   │ 0.6     │ 3.0     │ 43.6458 │ 0.02    │

In [584]:
JointEq.identify_matching_row(fidf, epst.jf.sf)

2-element BitArray{1}:
  true
 false

In [585]:
JointEq.identify_matching_row(fidf, epst.jf.rf)

2-element BitArray{1}:
 false
  true

In [588]:
fidfrow = JointEq.slice_full_info_dataframe(fidf, epst.jf.jks, epst.jf.sf; rerun=false)

Match found!
Extracting row...


1×27 DataFrame. Omitted printing of 21 columns
│ Row │ ROE     │ V0      │ alpha   │ c       │ debt    │ delta   │
│     │ Float64 │ Float64 │ Float64 │ Float64 │ Float64 │ Float64 │
├─────┼─────────┼─────────┼─────────┼─────────┼─────────┼─────────┤
│ 1   │ 27.5335 │ 100.0   │ 0.6     │ 3.0     │ 56.76   │ 0.0199  │

In [589]:
fidfrow = JointEq.slice_full_info_dataframe(fidf, epst.jf.jks, epst.jf.rf; rerun=false)

Match found!
Extracting row...


1×27 DataFrame. Omitted printing of 20 columns
│ Row │ ROE     │ V0      │ alpha   │ c       │ debt    │ delta   │ eq_deriv   │
│     │ Float64 │ Float64 │ Float64 │ Float64 │ Float64 │ Float64 │ Float64    │
├─────┼─────────┼─────────┼─────────┼─────────┼─────────┼─────────┼────────────┤
│ 1   │ 13.2612 │ 100.0   │ 0.6     │ 3.0     │ 43.6458 │ 0.02    │ 2.21491e-5 │

In [591]:
misrepdf_name = "misrepdf"
misrepdf = JointEq.reshape_sf_rf_df(epst.misrep)
ep_ks_path = JointEq.get_ep_results_path(epst.jf)
misrep_col_types = vcat(Bool, fill(Float64, 11), Bool,
                        fill(Float64, 15), Bool, fill(Float64, 17))

if !JointEq.exists_ep_df(epst.jf, misrepdf_name)
    CSV.write(string(ep_ks_path, "/", misrepdf_name, ".csv"), misrepdf)
else
    misrepdf = CSV.read(string(ep_ks_path, "/", misrepdf_name, ".csv"); types=misrep_col_types) 
end

1×46 DataFrame. Omitted printing of 40 columns
│ Row │ sf_defaults_first │ kappa   │ mu_s    │ m       │ c       │ p       │
│     │ Bool              │ Float64 │ Float64 │ Float64 │ Float64 │ Float64 │
├─────┼───────────────────┼─────────┼─────────┼─────────┼─────────┼─────────┤
│ 1   │ false             │ 0.0025  │ 1.0     │ 1.0     │ 3.0     │ 35.0    │

In [593]:
misrep_jks = deepcopy(epst.jf.jks)
setfield!(misrep_jks, :mu_s, 1.)
setfield!(misrep_jks, :mu_b, fi_sf_mu_b)
JointEq.slice_misrep_dataframe(misrepdf, misrep_jks, epst.jf; rerun=false)

Match found!
Extracting row...


1×46 DataFrame. Omitted printing of 40 columns
│ Row │ sf_defaults_first │ kappa   │ mu_s    │ m       │ c       │ p       │
│     │ Bool              │ Float64 │ Float64 │ Float64 │ Float64 │ Float64 │
├─────┼───────────────────┼─────────┼─────────┼─────────┼─────────┼─────────┤
│ 1   │ false             │ 0.0025  │ 1.0     │ 1.0     │ 3.0     │ 35.0    │

In [577]:
JointEq.reshape_sf_rf_df(epst.pool)

1×46 DataFrame. Omitted printing of 40 columns
│ Row │ sf_defaults_first │ kappa   │ mu_s    │ m       │ c       │ p       │
│     │ Bool              │ Float64 │ Float64 │ Float64 │ Float64 │ Float64 │
├─────┼───────────────────┼─────────┼─────────┼─────────┼─────────┼─────────┤
│ 1   │ false             │ 0.0025  │ 0.5     │ 1.0     │ 3.0     │ 35.0    │

In [602]:
pooldf_name = "pooldf"
pooldf = JointEq.reshape_sf_rf_df(epst.pool)
ep_ks_path = JointEq.get_ep_results_path(epst.jf)
mps_col_types = vcat(Bool, fill(Float64, 11), Bool,
                     fill(Float64, 15), Bool, fill(Float64, 17))

if !JointEq.exists_ep_df(epst.jf, pooldf_name)
    CSV.write(string(ep_ks_path, "/", pooldf_name, ".csv"), pooldf)
else
    pooldf = CSV.read(string(ep_ks_path, "/", pooldf_name, ".csv"); types=mps_col_types) 
end

1×46 DataFrame. Omitted printing of 40 columns
│ Row │ sf_defaults_first │ kappa   │ mu_s    │ m       │ c       │ p       │
│     │ Bool              │ Float64 │ Float64 │ Float64 │ Float64 │ Float64 │
├─────┼───────────────────┼─────────┼─────────┼─────────┼─────────┼─────────┤
│ 1   │ false             │ 0.0025  │ 0.5     │ 1.0     │ 3.0     │ 35.0    │

In [604]:
sepdf_name = "sepdf"
sepdf = JointEq.reshape_sf_rf_df(epst.sep)
ep_ks_path = JointEq.get_ep_results_path(epst.jf)
mps_col_types = vcat(Bool, fill(Float64, 11), Bool,
                     fill(Float64, 15), Bool, fill(Float64, 17))

if !JointEq.exists_ep_df(epst.jf, sepdf_name)
    CSV.write(string(ep_ks_path, "/", sepdf_name, ".csv"), sepdf)
else
    sepdf = CSV.read(string(ep_ks_path, "/", sepdf_name, ".csv"); types=mps_col_types) 
end

1×46 DataFrame. Omitted printing of 40 columns
│ Row │ sf_defaults_first │ kappa   │ mu_s    │ m       │ c       │ p       │
│     │ Bool              │ Float64 │ Float64 │ Float64 │ Float64 │ Float64 │
├─────┼───────────────────┼─────────┼─────────┼─────────┼─────────┼─────────┤
│ 1   │ false             │ 0.0025  │ 0.5     │ 1.0     │ 3.0     │ 35.0    │

In [794]:
modls = ["ModelObj", "AnalyticFunctions", "BondPrInterp", 
         "EqFinDiff", "Batch","JointEq"]
for modl in modls
    include(string(joinpath(module_path, modl), "/", modl, ".jl"))
end

In [775]:
# Measure of Firms and Standardized Bond
ep_jks = JointEq.store_ep_params(jep.mu_s;
                         ep_m=ep_m,
                         ep_c=ep_c,
                         ep_p=ep_p)

# epst3 

epst4 = JointEq.ep_constructor(jep, sf_bt, rf_bt; ep_jks=ep_jks,
                                rerun_full_info=false,
                                rerun_misrep=false,
                                rerun_pool=true,    
                                rerun_sep=false)

Setting parameter dictionary to batch object's parameter dictionary
Setting parameter values... 
Setting parameter dictionary using unique combination ID...
Setting initial vbl value to NaN
Setting initial vbh value to NaN
Setting initial c value to NaN
Setting initial p value to NaN
Constant Volatility Model: setting vbh to vbl, lambda to NaN
Setting parameter dictionary to batch object's parameter dictionary
Setting parameter values... 
Setting parameter dictionary using unique combination ID...
Batch object exists: true
Loading SVM object...
Unable to load batch object file.
Batch Object is incompatible! Loading surfaces only instead.
Setting initial vbl value to NaN
Setting initial vbh value to NaN
Setting initial c value to NaN
Setting initial p value to NaN
Interpolating Bond Pricing Surfaces...
  0.278791 seconds (811.43 k allocations: 137.115 MiB, 34.97% gc time)
Interpolating bond pricing surfaces...
  0.564040 seconds (811.43 k allocations: 137.113 MiB, 67.95% gc time)
Match 

Computing equity values... 
V0: 100.0; equity: 74.10319201434814
Equity Core Function Computation Time: 0.31983113288879395
Total Equity FD Core Function Computation Time: 0.4386920928955078
Total computation time: 0.468825101852417
Computing Equity Vmax
Vmax: 125.0
phi0: -24.3024931580549
phi1: 0.9999999999999998
pv_rfdebt: 32.734334816060915
debt_abs_per_diff: 1.247203899401134e-6
eq_abs_per_diff: 0.0009794519058781575
Equity Vmax: 286.50228972512923
 
eq_max: 262.1996375637732
eq_vbl: 0.0
Computing Constant Volatility Equity Values
Finished computing Constant Volatility Equity Values
Time to compute Constant Volatility Equity Values: 0.008098125457763672
 
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 74.0856096649717
Equity Core Function Computation Time: 0.04228019714355469
Total Equity FD Core Function Computation Time: 0.11394810676574707
Total computation time: 0.14409899711608887
Computing Equity Vmax
Vmax: 125.0
phi0: -24.3024931580549
phi1: 0.

Computing equity values... 
V0: 100.0; equity: 74.23114801696421
Equity Core Function Computation Time: 0.3184201717376709
Total Equity FD Core Function Computation Time: 0.4356839656829834
Total computation time: 0.4653499126434326
Computing Equity Vmax
Vmax: 125.0
phi0: -24.3024931580549
phi1: 0.9999999999999998
pv_rfdebt: 32.734334816060915
debt_abs_per_diff: 1.247203899401134e-6
eq_abs_per_diff: 0.0009794519058781575
Equity Vmax: 286.50228972512923
 
eq_max: 262.1996375637732
eq_vbl: 0.0
Computing Constant Volatility Equity Values
Finished computing Constant Volatility Equity Values
Time to compute Constant Volatility Equity Values: 0.00802302360534668
 
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 74.22281862380753
Equity Core Function Computation Time: 0.04194307327270508
Total Equity FD Core Function Computation Time: 0.1138148307800293
Total computation time: 0.14338397979736328
Computing Equity Vmax
Vmax: 125.0
phi0: -24.3024931580549
phi1: 0.9

Computing equity values... 
V0: 100.0; equity: 74.05235897257661
Equity Core Function Computation Time: 0.31844210624694824
Total Equity FD Core Function Computation Time: 0.436176061630249
Total computation time: 0.4663429260253906
Computing Equity Vmax
Vmax: 125.0
phi0: -24.3024931580549
phi1: 0.9999999999999998
pv_rfdebt: 32.734334816060915
debt_abs_per_diff: 1.247203899401134e-6
eq_abs_per_diff: 0.0009794519058781575
Equity Vmax: 286.50228972512923
 
eq_max: 262.1996375637732
eq_vbl: 0.0
Computing Constant Volatility Equity Values
Finished computing Constant Volatility Equity Values
Time to compute Constant Volatility Equity Values: 0.008131980895996094
 
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 74.04767792635566
Equity Core Function Computation Time: 0.04213714599609375
Total Equity FD Core Function Computation Time: 0.11364507675170898
Total computation time: 0.1438310146331787
Computing Equity Vmax
Vmax: 125.0
phi0: -24.3024931580549
phi1: 0.

Computing equity values... 
V0: 100.0; equity: 75.04295488011364
Equity Core Function Computation Time: 0.042012929916381836
Total Equity FD Core Function Computation Time: 0.1042940616607666
Computing Constant Volatility Equity Values
Finished computing Constant Volatility Equity Values
Time to compute Constant Volatility Equity Values: 0.008083105087280273
 
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 74.2037071393375
Equity Core Function Computation Time: 0.042860984802246094
Total Equity FD Core Function Computation Time: 0.12370419502258301
Total computation time: 0.2832000255584717
Computing Equity Vmax
Vmax: 125.0
phi0: -24.3024931580549
phi1: 0.9949999999999999
pv_rfdebt: 32.734334816060915
debt_abs_per_diff: NaN
eq_abs_per_diff: NaN
Vmax: 125.0
phi0: -24.3024931580549
phi1: 0.9999999999999998
pv_rfdebt: 32.734334816060915
debt_abs_per_diff: 1.247203899401134e-6
eq_abs_per_diff: 0.0009794519058781575
Equity Vmax: 286.50228972512923
 
eq_max: 2.

...

Computing equity values... 
V0: 100.0; equity: 67.08341164998022
Equity Core Function Computation Time: 0.31764888763427734
Total Equity FD Core Function Computation Time: 0.4270329475402832
Computing Constant Volatility Equity Values
Finished computing Constant Volatility Equity Values
Time to compute Constant Volatility Equity Values: 0.008126020431518555
 
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 64.77491092487917
Equity Core Function Computation Time: 0.04194808006286621
Total Equity FD Core Function Computation Time: 0.11220312118530273
Total computation time: 0.7020142078399658
Computing Equity Vmax
Vmax: 125.0
phi0: -31.7689086346845
phi1: 0.9949999999999999
pv_rfdebt: 42.79125130188265
debt_abs_per_diff: NaN
eq_abs_per_diff: NaN
Vmax: 125.0
phi0: -31.7689086346845
phi1: 0.9999999999999998
pv_rfdebt: 42.79125130188265
debt_abs_per_diff: 1.5490584165496826e-7
eq_abs_per_diff: 0.0009042696951821385
Equity Vmax: 383.9404694897265
 
eq_max: 2.042

Computing equity values... 
V0: 100.0; equity: 64.73652919462697
Equity Core Function Computation Time: 0.042593955993652344
Total Equity FD Core Function Computation Time: 0.12317013740539551
Total computation time: 0.402263879776001
Computing Equity Vmax
Vmax: 125.0
phi0: -31.7689086346845
phi1: 0.9949999999999999
pv_rfdebt: 42.79125130188265
debt_abs_per_diff: NaN
eq_abs_per_diff: NaN
Vmax: 125.0
phi0: -31.7689086346845
phi1: 0.9999999999999998
pv_rfdebt: 42.79125130188265
debt_abs_per_diff: 1.5490584165496826e-7
eq_abs_per_diff: 0.0009042696951821385
Equity Vmax: 383.9404694897265
 
eq_max: 2.1369633071876177
eq_vbl: 0.0
eq_vbl: 0.0
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 67.13611788271992
Equity Core Function Computation Time: 0.317302942276001
Total Equity FD Core Function Computation Time: 0.42357516288757324
Computing Constant Volatility Equity Values
Finished computing Constant Volatility Equity Values
Time to compute Constant Volatility E

Excessive output truncated after 524306 bytes.

V0: 100.0; equity: 64.7810699049618
Equity Core Function Computation Time: 0.042021989822387695
Total Equity FD Core Function Computation Time: 0.1123659610748291
Total computation time: 0.5853569507598877
Computing Equity Vmax
Vmax: 125.0
phi0: -31.7689086346845
phi1: 0.9949999999999999
pv_rfdebt: 42.79125130188265


MethodError: MethodError: no method matching iterate(::RemoteException)
Closest candidates are:
  iterate(!Matched::Core.SimpleVector) at essentials.jl:568
  iterate(!Matched::Core.SimpleVector, !Matched::Any) at essentials.jl:568
  iterate(!Matched::ExponentialBackOff) at error.jl:199
  ...

In [781]:
sf_obj_fun = :firm_value
rf_obj_fun = :ROE

# Capture Full Information Optimal mu_b and ROE ###################
fi_sf_mu_b = epst5.sfdf[1, :mu_b]
fi_rf_mu_b = epst5.rfdf[1, :mu_b]
fi_sf_obj_val = epst5.sfdf[1, sf_obj_fun]
fi_rf_obj_val = epst5.rfdf[1, rf_obj_fun]
# #################################################################

rerun_pool = true

ep_jf = deepcopy(epst5.jf)

Main.JointEq.JointFirms(Main.JointEq.JointKStruct(0.5, NaN, 1.0, 3.0, 35.0, NaN, NaN, NaN, NaN, NaN), ModelObj.Firm
  mu_b: Float64 1.0
  m: Float64 1.0
  c: Float64 NaN
  p: Float64 NaN
  vbl: Float64 NaN
  vbh: Float64 NaN
  pm: ModelObj.FirmParams
  model: String "cvm"
  bi: ModelObj.BPrInputs
  bs: ModelObj.BPrSurfs
  bf: ModelObj.BPrInterpFuns
  bit: ModelObj.BPrFixedTTMInputs
  bft: ModelObj.BPrInterpFuns
  optKS: ModelObj.KStruct
, ModelObj.Firm
  mu_b: Float64 1.0
  m: Float64 1.0
  c: Float64 NaN
  p: Float64 NaN
  vbl: Float64 NaN
  vbh: Float64 NaN
  pm: ModelObj.FirmParams
  model: String "svm"
  bi: ModelObj.BPrInputs
  bs: ModelObj.BPrSurfs
  bf: ModelObj.BPrInterpFuns
  bit: ModelObj.BPrFixedTTMInputs
  bft: ModelObj.BPrInterpFuns
  optKS: ModelObj.KStruct
, Batch.BatchStruct
  model: String "cvm"
  dfn: Batch.DirFileNames
  dfc: Batch.BatchDFColumns
  mi: Batch.ModelInputs
  bp: Batch.BatchParams
  coupon_grid: Array{Float64}((26,)) [0.25, 0.5, 1.0, 1.5, 2.0, 2.5, 3.0, 

In [804]:
epst2.pool = ep_pool_eqdf
epst2.sep = ep_sep_eqdf

1×48 DataFrame. Omitted printing of 42 columns
│ Row │ sf_defaults_first │ kappa   │ mu_s    │ m       │ c       │ p       │
│     │ Bool              │ Float64 │ Float64 │ Float64 │ Float64 │ Float64 │
├─────┼───────────────────┼─────────┼─────────┼─────────┼─────────┼─────────┤
│ 1   │ false             │ 0.0025  │ 1.0     │ 1.0     │ 3.0     │ 35.0    │

In [790]:
ep_pool_eqdf = JointEq.ep_pool_misrep_eq(ep_jf, ep_jks,
                             fi_sf_mu_b,
                             fi_rf_mu_b,
                             fi_rf_obj_val,
                             ep_ks_path;
                             equilibrium_type="pooling",
                             rerun=true)


Computing Pooling Equilibrium
Computing Equity Vmax
Vmax: 125.0
phi0: -24.3024931580549
phi1: 0.9999999999999998
pv_rfdebt: 32.734334816060915
debt_abs_per_diff: 1.247203899401134e-6
eq_abs_per_diff: 0.0009794519058781575
Equity Vmax: 286.50228972512923
 
eq_max: 262.1996375637732
eq_vbl: 0.0
Computing Constant Volatility Equity Values
Finished computing Constant Volatility Equity Values
Time to compute Constant Volatility Equity Values: 0.0728299617767334
 
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 74.24304583073739
Equity Core Function Computation Time: 0.04343819618225098
Total Equity FD Core Function Computation Time: 0.266481876373291
Total computation time: 0.8860809803009033
Computing Equity Vmax
Vmax: 125.0
phi0: -24.3024931580549
phi1: 0.9999999999999998
pv_rfdebt: 32.734334816060915
debt_abs_per_diff: 1.247203899401134e-6
eq_abs_per_diff: 0.0009794519058781575
Equity Vmax: 286.50228972512923
 
eq_max: 262.1996375637733
eq_vbl: 0.0
Computing

Computing equity values... 
V0: 100.0; equity: 74.0856096649717
Equity Core Function Computation Time: 0.043853044509887695
Total Equity FD Core Function Computation Time: 0.12985992431640625
Total computation time: 0.16006684303283691
Computing Equity Vmax
Vmax: 125.0
phi0: -24.3024931580549
phi1: 0.9999999999999998
pv_rfdebt: 32.734334816060915
debt_abs_per_diff: 1.247203899401134e-6
eq_abs_per_diff: 0.0009794519058781575
Equity Vmax: 286.50228972512923
 
eq_max: 262.1996375637732
eq_vbl: 0.0
Computing Constant Volatility Equity Values
Finished computing Constant Volatility Equity Values
Time to compute Constant Volatility Equity Values: 0.00810098648071289
 
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 74.07116403660052
Equity Core Function Computation Time: 0.04636788368225098
Total Equity FD Core Function Computation Time: 0.12053108215332031
Total computation time: 0.15076494216918945
Computing Equity Vmax
Vmax: 125.0
phi0: -24.3024931580549
phi1:

Computing equity values... 
V0: 100.0; equity: 74.22281862380753
Equity Core Function Computation Time: 0.04366588592529297
Total Equity FD Core Function Computation Time: 0.12911105155944824
Total computation time: 0.1588129997253418
Computing Equity Vmax
Vmax: 125.0
phi0: -24.3024931580549
phi1: 0.9999999999999998
pv_rfdebt: 32.734334816060915
debt_abs_per_diff: 1.247203899401134e-6
eq_abs_per_diff: 0.0009794519058781575
Equity Vmax: 286.50228972512923
 
eq_max: 262.1996375637733
eq_vbl: 0.0
Computing Constant Volatility Equity Values
Finished computing Constant Volatility Equity Values
Time to compute Constant Volatility Equity Values: 0.008035898208618164
 
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 74.2125358069307
Equity Core Function Computation Time: 0.045979976654052734
Total Equity FD Core Function Computation Time: 0.11956000328063965
Total computation time: 0.1493690013885498
Computing Equity Vmax
Vmax: 125.0
phi0: -24.3024931580549
phi1: 

Computing equity values... 
V0: 100.0; equity: 74.04767792635566
Equity Core Function Computation Time: 0.04331207275390625
Total Equity FD Core Function Computation Time: 0.12907004356384277
Total computation time: 0.15935206413269043
Computing Equity Vmax
Vmax: 125.0
phi0: -24.3024931580549
phi1: 0.9999999999999998
pv_rfdebt: 32.734334816060915
debt_abs_per_diff: 1.247203899401134e-6
eq_abs_per_diff: 0.0009794519058781575
Equity Vmax: 286.50228972512923
 
eq_max: 262.1996375637732
eq_vbl: 0.0
Computing Constant Volatility Equity Values
Finished computing Constant Volatility Equity Values
Time to compute Constant Volatility Equity Values: 0.008134841918945312
 
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 74.04564307501936
Equity Core Function Computation Time: 0.046196937561035156
Total Equity FD Core Function Computation Time: 0.11990690231323242
Total computation time: 0.15015482902526855
Computing Equity Vmax
Vmax: 125.0
phi0: -24.3024931580549
phi

V0: 100.0; equity: 74.2037071393375
Equity Core Function Computation Time: 0.04327797889709473
Total Equity FD Core Function Computation Time: 0.11697077751159668
Total computation time: 0.5947518348693848
Computing Equity Vmax
Vmax: 125.0
phi0: -24.3024931580549
phi1: 0.9949999999999999
pv_rfdebt: 32.734334816060915
debt_abs_per_diff: NaN
eq_abs_per_diff: NaN
Vmax: 125.0
phi0: -24.3024931580549
phi1: 0.9999999999999998
pv_rfdebt: 32.734334816060915
debt_abs_per_diff: 1.247203899401134e-6
eq_abs_per_diff: 0.0009794519058781575
Equity Vmax: 286.50228972512923
 
eq_max: 2.146034479946937
eq_vbl: 0.0
eq_vbl: 0.0
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 75.03141426447466
Equity Core Function Computation Time: 0.042878150939941406
Total Equity FD Core Function Computation Time: 0.10763096809387207
Computing Constant Volatility Equity Values
Finished computing Constant Volatility Equity Values
Time to compute Constant Volatility Equity Values: 0.008090019

...

Computing equity values... 
V0: 100.0; equity: 67.07678361946577
Equity Core Function Computation Time: 0.0458371639251709
Total Equity FD Core Function Computation Time: 0.11154007911682129
Computing Constant Volatility Equity Values
Finished computing Constant Volatility Equity Values
Time to compute Constant Volatility Equity Values: 0.008135795593261719
 
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 64.770001103836
Equity Core Function Computation Time: 0.3239560127258301
Total Equity FD Core Function Computation Time: 0.44506216049194336
Total computation time: 0.7329449653625488
Computing Equity Vmax
Vmax: 125.0
phi0: -31.7689086346845
phi1: 0.9949999999999999
pv_rfdebt: 42.79125130188265
debt_abs_per_diff: NaN
eq_abs_per_diff: NaN
Vmax: 125.0
phi0: -31.7689086346845
phi1: 0.9999999999999998
pv_rfdebt: 42.79125130188265
debt_abs_per_diff: 1.5490584165496826e-7
eq_abs_per_diff: 0.0009042696951821385
Equity Vmax: 383.9404694897265
 
eq_max: 2.030019

Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 67.05198827544298
Equity Core Function Computation Time: 0.042816877365112305
Total Equity FD Core Function Computation Time: 0.1073141098022461
Computing Constant Volatility Equity Values
Finished computing Constant Volatility Equity Values
Time to compute Constant Volatility Equity Values: 0.008121967315673828
 
Shape of Gamma matrix: (1498,)
Computing equity values... 


Excessive output truncated after 524294 bytes.

V0: 100.0; equity: 64.77289033981836
Equity Core Function Computation Time: 0.04298901557922363
Total Equity FD Core Function Computation Time: 0.1273059844970703
Total computation time: 0.2988548278808594
Computing Equity Vmax
Vmax: 125.0
phi0: -31.7689086346845
phi1: 0.9949999999999999
pv_rfdebt: 42.79125130188265


1×48 DataFrame. Omitted printing of 42 columns
│ Row │ sf_defaults_first │ kappa   │ mu_s    │ m       │ c       │ p       │
│     │ Bool              │ Float64 │ Float64 │ Float64 │ Float64 │ Float64 │
├─────┼───────────────────┼─────────┼─────────┼─────────┼─────────┼─────────┤
│ 1   │ false             │ 0.0025  │ 0.5     │ 1.0     │ 3.0     │ 35.0    │

In [796]:
ep_sep_eqdf = JointEq.ep_pool_misrep_eq(ep_jf, ep_jks,
                                        fi_sf_mu_b,
                                        fi_rf_f_mu_b,
                                        fi_rf_obj_val,
                                        ep_ks_path;
                                        equilibrium_type="separating",
                                        rerun=true)

Computing Separating Equilibrium
Computing Equity Vmax
Vmax: 125.0
phi0: -24.3024931580549
phi1: 0.9999999999999998
pv_rfdebt: 32.734334816060915
debt_abs_per_diff: 1.247203899401134e-6
eq_abs_per_diff: 0.0009794519058781575
Equity Vmax: 286.50228972512923
 
eq_max: 262.1996375637732
eq_vbl: 0.0
Computing Constant Volatility Equity Values
Finished computing Constant Volatility Equity Values
Time to compute Constant Volatility Equity Values: 0.0768880844116211
 
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 74.24304583073739
Equity Core Function Computation Time: 0.04558992385864258
Total Equity FD Core Function Computation Time: 0.28231096267700195
Total computation time: 0.9432101249694824
Computing Equity Vmax
Vmax: 125.0
phi0: -24.3024931580549
phi1: 0.9999999999999998
pv_rfdebt: 32.734334816060915
debt_abs_per_diff: 1.247203899401134e-6
eq_abs_per_diff: 0.0009794519058781575
Equity Vmax: 286.50228972512923
 
eq_max: 262.1996375637733
eq_vbl: 0.0
Comp

Computing equity values... 
V0: 100.0; equity: 74.0856096649717
Equity Core Function Computation Time: 0.045989036560058594
Total Equity FD Core Function Computation Time: 0.13679099082946777
Total computation time: 0.1671891212463379
Computing Equity Vmax
Vmax: 125.0
phi0: -24.3024931580549
phi1: 0.9999999999999998
pv_rfdebt: 32.734334816060915
debt_abs_per_diff: 1.247203899401134e-6
eq_abs_per_diff: 0.0009794519058781575
Equity Vmax: 286.50228972512923
 
eq_max: 262.1996375637732
eq_vbl: 0.0
Computing Constant Volatility Equity Values
Finished computing Constant Volatility Equity Values
Time to compute Constant Volatility Equity Values: 0.00810694694519043
 
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 74.07116403660052
Equity Core Function Computation Time: 0.048094987869262695
Total Equity FD Core Function Computation Time: 0.1247868537902832
Total computation time: 0.1552138328552246
Computing Equity Vmax
Vmax: 125.0
phi0: -24.3024931580549
phi1: 0

Computing equity values... 
V0: 100.0; equity: 74.22281862380753
Equity Core Function Computation Time: 0.04392194747924805
Total Equity FD Core Function Computation Time: 0.13028502464294434
Total computation time: 0.16002202033996582
Computing Equity Vmax
Vmax: 125.0
phi0: -24.3024931580549
phi1: 0.9999999999999998
pv_rfdebt: 32.734334816060915
debt_abs_per_diff: 1.247203899401134e-6
eq_abs_per_diff: 0.0009794519058781575
Equity Vmax: 286.50228972512923
 
eq_max: 262.1996375637733
eq_vbl: 0.0
Computing Constant Volatility Equity Values
Finished computing Constant Volatility Equity Values
Time to compute Constant Volatility Equity Values: 0.008036136627197266
 
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 74.2125358069307
Equity Core Function Computation Time: 0.04614996910095215
Total Equity FD Core Function Computation Time: 0.1204080581665039
Total computation time: 0.15009284019470215
Computing Equity Vmax
Vmax: 125.0
phi0: -24.3024931580549
phi1: 

Computing equity values... 
V0: 100.0; equity: 74.04767792635566
Equity Core Function Computation Time: 0.043685197830200195
Total Equity FD Core Function Computation Time: 0.13036298751831055
Total computation time: 0.16069388389587402
Computing Equity Vmax
Vmax: 125.0
phi0: -24.3024931580549
phi1: 0.9999999999999998
pv_rfdebt: 32.734334816060915
debt_abs_per_diff: 1.247203899401134e-6
eq_abs_per_diff: 0.0009794519058781575
Equity Vmax: 286.50228972512923
 
eq_max: 262.1996375637732
eq_vbl: 0.0
Computing Constant Volatility Equity Values
Finished computing Constant Volatility Equity Values
Time to compute Constant Volatility Equity Values: 0.008146047592163086
 
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 74.04564307501936
Equity Core Function Computation Time: 0.046243906021118164
Total Equity FD Core Function Computation Time: 0.12088680267333984
Total computation time: 0.15120506286621094
Computing Equity Vmax
Vmax: 125.0
phi0: -24.3024931580549
ph

V0: 100.0; equity: 74.25878675271366
Equity Core Function Computation Time: 0.04352617263793945
Total Equity FD Core Function Computation Time: 0.1176140308380127
Total computation time: 0.6015129089355469
Computing Equity Vmax
Vmax: 125.0
phi0: -24.3024931580549
phi1: 0.9949999999999999
pv_rfdebt: 32.734334816060915
debt_abs_per_diff: NaN
eq_abs_per_diff: NaN
Vmax: 125.0
phi0: -24.3024931580549
phi1: 0.9999999999999998
pv_rfdebt: 32.734334816060915
debt_abs_per_diff: 1.247203899401134e-6
eq_abs_per_diff: 0.0009794519058781575
Equity Vmax: 286.50228972512923
 
eq_max: 2.146034479946937
eq_vbl: 0.0
eq_vbl: 0.0
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 75.15021713161678
Equity Core Function Computation Time: 0.04322409629821777
Total Equity FD Core Function Computation Time: 0.10908794403076172
Computing Constant Volatility Equity Values
Finished computing Constant Volatility Equity Values
Time to compute Constant Volatility Equity Values: 0.0080900192

...

Computing equity values... 
V0: 100.0; equity: 67.38810672006575
Equity Core Function Computation Time: 0.046838998794555664
Total Equity FD Core Function Computation Time: 0.11348700523376465
Computing Constant Volatility Equity Values
Finished computing Constant Volatility Equity Values
Time to compute Constant Volatility Equity Values: 0.00820016860961914
 
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 64.87685027392791
Equity Core Function Computation Time: 0.3301248550415039
Total Equity FD Core Function Computation Time: 0.452739953994751
Total computation time: 0.7444038391113281
Computing Equity Vmax
Vmax: 125.0
phi0: -31.7689086346845
phi1: 0.9949999999999999
pv_rfdebt: 42.79125130188265
debt_abs_per_diff: NaN
eq_abs_per_diff: NaN
Vmax: 125.0
phi0: -31.7689086346845
phi1: 0.9999999999999998
pv_rfdebt: 42.79125130188265
debt_abs_per_diff: 1.5490584165496826e-7
eq_abs_per_diff: 0.0009042696951821385
Equity Vmax: 383.9404694897265
 
eq_max: 2.03001

Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 67.2758035613665
Equity Core Function Computation Time: 0.04329514503479004
Total Equity FD Core Function Computation Time: 0.1089780330657959
Computing Constant Volatility Equity Values
Finished computing Constant Volatility Equity Values
Time to compute Constant Volatility Equity Values: 0.008127927780151367
 
Shape of Gamma matrix: (1498,)
Computing equity values... 


Excessive output truncated after 524309 bytes.

V0: 100.0; equity: 64.86589330443395
Equity Core Function Computation Time: 0.04371190071105957
Total Equity FD Core Function Computation Time: 0.12931203842163086
Total computation time: 0.3031179904937744
Computing Equity Vmax
Vmax: 125.0
phi0: -31.7689086346845
phi1: 0.9949999999999999
pv_rfdebt: 42.79125130188265
debt_abs_per_diff: NaN
eq_abs_per_diff: NaN
Vmax: 125.0


1×48 DataFrame. Omitted printing of 42 columns
│ Row │ sf_defaults_first │ kappa   │ mu_s    │ m       │ c       │ p       │
│     │ Bool              │ Float64 │ Float64 │ Float64 │ Float64 │ Float64 │
├─────┼───────────────────┼─────────┼─────────┼─────────┼─────────┼─────────┤
│ 1   │ false             │ 0.0025  │ 1.0     │ 1.0     │ 3.0     │ 35.0    │

In [797]:
epst3.sep

1×46 DataFrame. Omitted printing of 40 columns
│ Row │ sf_defaults_first │ kappa   │ mu_s    │ m       │ c       │ p       │
│     │ Bool              │ Float64 │ Float64 │ Float64 │ Float64 │ Float64 │
├─────┼───────────────────┼─────────┼─────────┼─────────┼─────────┼─────────┤
│ 1   │ false             │ 0.0025  │ 0.5     │ 1.0     │ 3.0     │ 35.0    │

In [725]:
fidf_name = "fidf"
ep_ks_path = JointEq.get_ep_results_path(epst.jf)
fidf_col_types = vcat(fill(Float64, 9), [Bool], fill(Float64, 17))
if !JointEq.exists_ep_df(ep_ks_path, fidf_name)
    CSV.write(string(ep_ks_path, "/", fidf_name, ".csv"), vcat(epst.sfdf, epst.rfdf))
else
    fidf = CSV.read(string(ep_ks_path, "/", fidf_name, ".csv"); types=dfcols) 
end

2×27 DataFrame. Omitted printing of 21 columns
│ Row │ ROE     │ V0      │ alpha   │ c       │ debt    │ delta   │
│     │ Float64 │ Float64 │ Float64 │ Float64 │ Float64 │ Float64 │
├─────┼─────────┼─────────┼─────────┼─────────┼─────────┼─────────┤
│ 1   │ 27.5335 │ 100.0   │ 0.6     │ 3.0     │ 56.76   │ 0.0199  │
│ 2   │ 13.2612 │ 100.0   │ 0.6     │ 3.0     │ 43.6458 │ 0.02    │

In [866]:
modls = ["ModelObj", "AnalyticFunctions", "BondPrInterp", 
         "EqFinDiff", "Batch","JointEq"]
for modl in modls
    include(string(joinpath(module_path, modl), "/", modl, ".jl"))
end

In [864]:


CSV.read(string(ep_ks_path, "/", JointEq.sepdf_name, ".csv");
                        types=JointEq.mps_col_types)


MethodError: MethodError: no method matching defaultparser(::Base.GenericIOBuffer{Array{UInt8,1}}, ::Parsers.Result{Symbol})
Closest candidates are:
  defaultparser(::IO, !Matched::Parsers.Result{Bool}; bools, kwargs...) at /home/artur/.julia/packages/Parsers/GKxCA/src/Parsers.jl:787
  defaultparser(::IO, !Matched::Parsers.Result{Union{}}; kwargs...) at /home/artur/.julia/packages/Parsers/GKxCA/src/Parsers.jl:796
  defaultparser(::IO, !Matched::Parsers.Result{T<:Integer}; kwargs...) where T<:Integer at /home/artur/.julia/packages/Parsers/GKxCA/src/Parsers.jl:743
  ...

In [860]:
epst2.misrep[:s_obj_fun] = String.(epst2.misrep[:s_obj_fun])
epst2.misrep[:r_obj_fun] = String.(epst2.misrep[:r_obj_fun])
epst2.pool[:s_obj_fun] = String.(epst2.pool[:s_obj_fun])
epst2.pool[:r_obj_fun] = String.(epst2.pool[:r_obj_fun])
epst2.sep[:s_obj_fun] = String.(epst2.sep[:s_obj_fun])
epst2.sep[:r_obj_fun] = String.(epst2.sep[:r_obj_fun])

1-element Array{String,1}:
 "ROE"

In [862]:
dfdict = Dict(:sfdf => [JointEq.fidf_name, epst2.sfdf], 
              :rfdf => [JointEq.fidf_name, epst2.rfdf],
              :misrep => [JointEq.misrepdf_name, epst2.misrep],
              :pool => [JointEq.pooldf_name, epst2.pool],
              :sep => [JointEq.sepdf_name, epst2.sep])

for key in keys(dfdict)
    println(key)
    JointEq.update_file(ep_ks_path, dfdict[key][1], dfdict[key][2])
end


sep


MethodError: MethodError: no method matching defaultparser(::Base.GenericIOBuffer{Array{UInt8,1}}, ::Parsers.Result{Symbol})
Closest candidates are:
  defaultparser(::IO, !Matched::Parsers.Result{Bool}; bools, kwargs...) at /home/artur/.julia/packages/Parsers/GKxCA/src/Parsers.jl:787
  defaultparser(::IO, !Matched::Parsers.Result{Union{}}; kwargs...) at /home/artur/.julia/packages/Parsers/GKxCA/src/Parsers.jl:796
  defaultparser(::IO, !Matched::Parsers.Result{T<:Integer}; kwargs...) where T<:Integer at /home/artur/.julia/packages/Parsers/GKxCA/src/Parsers.jl:743
  ...

"misrepdf"

In [667]:
dfrow = DataFrame(epst2.sfdf[1, :])
dfrow[1, :ROE] = 30.
resdf[row_cond, :] = DataFrame(dfrow[1, :])

1×27 DataFrame. Omitted printing of 21 columns
│ Row │ ROE     │ V0      │ alpha   │ c       │ debt    │ delta   │
│     │ Float64 │ Float64 │ Float64 │ Float64 │ Float64 │ Float64 │
├─────┼─────────┼─────────┼─────────┼─────────┼─────────┼─────────┤
│ 1   │ 30.0    │ 100.0   │ 0.6     │ 3.0     │ 56.76   │ 0.0199  │

In [668]:
resdf

2×27 DataFrame. Omitted printing of 21 columns
│ Row │ ROE     │ V0      │ alpha   │ c       │ debt    │ delta   │
│     │ Float64 │ Float64 │ Float64 │ Float64 │ Float64 │ Float64 │
├─────┼─────────┼─────────┼─────────┼─────────┼─────────┼─────────┤
│ 1   │ 30.0    │ 100.0   │ 0.6     │ 3.0     │ 56.76   │ 0.0199  │
│ 2   │ 13.2612 │ 100.0   │ 0.6     │ 3.0     │ 43.6458 │ 0.02    │

In [639]:
nrow(fidf)

2

In [653]:
fidf = CSV.read(string(ep_ks_path, "/", "fidf", ".csv"); types=JointEq.fidf_col_types) 

2×27 DataFrame. Omitted printing of 21 columns
│ Row │ ROE     │ V0      │ alpha   │ c       │ debt    │ delta   │
│     │ Float64 │ Float64 │ Float64 │ Float64 │ Float64 │ Float64 │
├─────┼─────────┼─────────┼─────────┼─────────┼─────────┼─────────┤
│ 1   │ 27.5335 │ 100.0   │ 0.6     │ 3.0     │ 56.76   │ 0.0199  │
│ 2   │ 13.2612 │ 100.0   │ 0.6     │ 3.0     │ 43.6458 │ 0.02    │

In [657]:
row_cond = identify_match(fidf, DataFrame(epst2.sfdf))

2-element BitArray{1}:
  true
 false

In [651]:
epst2.sfdf

1×27 DataFrame. Omitted printing of 21 columns
│ Row │ ROE     │ V0      │ alpha   │ c       │ debt    │ delta   │
│     │ Float64 │ Float64 │ Float64 │ Float64 │ Float64 │ Float64 │
├─────┼─────────┼─────────┼─────────┼─────────┼─────────┼─────────┤
│ 1   │ 27.5335 │ 100.0   │ 0.6     │ 3.0     │ 56.76   │ 0.0199  │

In [66]:
?JointEq.joint_firm_constructor()

No documentation found.

`Main.JointEq.joint_firm_constructor` is a `Function`.

```
# 1 method for generic function "joint_firm_constructor":
[1] joint_firm_constructor(safe::ModelObj.Firm, risky::ModelObj.Firm; jks, m, load_results_dfs, opt_k_struct_df_name, svm_coltypes, recompute_svm) in Main.JointEq at /home/artur/BondPricing/Julia/modules/JointEq/_joint_eq_constructors.jl:12
```


In [437]:
modls = ["ModelObj", "AnalyticFunctions", "BondPrInterp", 
         "EqFinDiff", "Batch","JointEq"]
for modl in modls
    include(string(joinpath(module_path, modl), "/", modl, ".jl"))
end

In [239]:
comb_num = 1
cbt, cvm = Batch.get_bt_cvm(;comb_num=comb_num)
sbt, svm = Batch.get_bt_svm(;comb_num=comb_num)
jf = JointEq.joint_firm_constructor(cvm, svm; m=1., load_results_dfs=true)

Setting parameter dictionary using unique combination ID...
Setting initial vbl value to NaN
Setting initial vbh value to NaN
Setting initial c value to NaN
Setting initial p value to NaN
Constant Volatility Model: setting vbh to vbl, lambda to NaN
Setting parameter dictionary using unique combination ID...
Batch object exists: true
Loading SVM object...
Unable to load batch object file.
Batch Object is incompatible! Loading surfaces only instead.
Setting initial vbl value to NaN
Setting initial vbh value to NaN
Setting initial c value to NaN
Setting initial p value to NaN
Interpolating Bond Pricing Surfaces...
  0.212225 seconds (811.43 k allocations: 137.113 MiB, 17.25% gc time)
Interpolating bond pricing surfaces...
  0.201871 seconds (811.43 k allocations: 137.113 MiB, 15.85% gc time)
Loading optimal results dataframe...
Setting parameter dictionary using (m, m_comb_num) ID pair...
Loading optimal results dataframe...


Main.JointEq.JointFirms(Main.JointEq.JointKStruct(NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN), ModelObj.Firm
  mu_b: Float64 1.0
  m: Float64 1.0
  c: Float64 NaN
  p: Float64 NaN
  vbl: Float64 NaN
  vbh: Float64 NaN
  pm: ModelObj.FirmParams
  model: String "cvm"
  bi: ModelObj.BPrInputs
  bs: ModelObj.BPrSurfs
  bf: ModelObj.BPrInterpFuns
  bit: ModelObj.BPrFixedTTMInputs
  bft: ModelObj.BPrInterpFuns
  optKS: ModelObj.KStruct
, ModelObj.Firm
  mu_b: Float64 1.0
  m: Float64 1.0
  c: Float64 NaN
  p: Float64 NaN
  vbl: Float64 NaN
  vbh: Float64 NaN
  pm: ModelObj.FirmParams
  model: String "svm"
  bi: ModelObj.BPrInputs
  bs: ModelObj.BPrSurfs
  bf: ModelObj.BPrInterpFuns
  bit: ModelObj.BPrFixedTTMInputs
  bft: ModelObj.BPrInterpFuns
  optKS: ModelObj.KStruct
, Batch.BatchStruct
  model: String "cvm"
  dfn: Batch.DirFileNames
  dfc: Batch.BatchDFColumns
  mi: Batch.ModelInputs
  bp: Batch.BatchParams
  coupon_grid: Array{Float64}((26,)) [0.25, 0.5, 1.0, 1.5, 2.0, 2.5, 3.0, 3

In [3]:
tmp = JointEq.find_risky_combinations(cvm)
tmp[tmp[:model].=="svm", :]

Setting parameter dictionary using unique combination ID...
Setting parameter dictionary using unique combination ID...


30×13 DataFrame. Omitted printing of 6 columns
│ Row │ match │ model  │ comb_num │ m       │ m_comb_num │ mu_b    │ xi      │
│     │ Bool  │ String │ Int64    │ Float64 │ Int64      │ Float64 │ Float64 │
├─────┼───────┼────────┼──────────┼─────────┼────────────┼─────────┼─────────┤
│ 1   │ false │ svm    │ 2        │ 1.0     │ 2          │ 1.0     │ 1.0     │
│ 2   │ false │ svm    │ 7        │ 1.0     │ 7          │ 1.0     │ 1.0     │
│ 3   │ false │ svm    │ 12       │ 1.0     │ 12         │ 1.0     │ 1.0     │
│ 4   │ false │ svm    │ 17       │ 1.0     │ 17         │ 1.0     │ 1.0     │
│ 5   │ false │ svm    │ 22       │ 1.0     │ 22         │ 1.0     │ 1.0     │
│ 6   │ false │ svm    │ 27       │ 1.0     │ 27         │ 1.0     │ 1.0     │
│ 7   │ false │ svm    │ 32       │ 1.0     │ 32         │ 1.0     │ 1.0     │
│ 8   │ false │ svm    │ 37       │ 1.0     │ 37         │ 1.0     │ 1.0     │
│ 9   │ false │ svm    │ 42       │ 1.0     │ 42         │ 1.0     │ 1.0     │
│ 10  │ false │ svm    │ 47       │ 1.0     │ 47         │ 1.0     │ 1.0     │
│ 11  │ false │ svm    │ 52       │ 1.0     │ 52         │ 1.0     │ 1.0     │
│ 12  │ false │ svm    │ 57       │ 1.0     │ 57         │ 1.0     │ 1.0     │
│ 13  │ false │ svm    │ 62       │ 1.0     │ 62         │ 1.0     │ 1.0     │
│ 14  │ false │ svm    │ 67       │ 1.0     │ 67         │ 1.0     │ 1.0     │
│ 15  │ false │ svm    │ 72       │ 1.0     │ 72         │ 1.0     │ 1.0     │
│ 16  │ false │ svm    │ 77       │ 1.0     │ 77         │ 1.0     │ 1.0     │
│ 17  │ false │ svm    │ 82       │ 1.0     │ 82         │ 1.0     │ 1.0     │
│ 18  │ false │ svm    │ 87       │ 1.0     │ 87         │ 1.0     │ 1.0     │
│ 19  │ false │ svm    │ 92       │ 1.0     │ 92         │ 1.0     │ 1.0     │
│ 20  │ false │ svm    │ 97       │ 1.0     │ 97         │ 1.0     │ 1.0     │
│ 21  │ false │ svm    │ 102      │ 1.0     │ 102        │ 1.0     │ 1.0     │
│ 22  │ false │ svm    │ 107      │ 1.0     │ 107        │ 1.0     │ 1.0     │
│ 23  │ false │ svm    │ 112      │ 1.0     │ 112        │ 1.0     │ 1.0     │
│ 24  │ false │ svm    │ 117      │ 1.0     │ 117        │ 1.0     │ 1.0     │
│ 25  │ false │ svm    │ 122      │ 1.0     │ 122        │ 1.0     │ 1.0     │
│ 26  │ false │ svm    │ 127      │ 1.0     │ 127        │ 1.0     │ 1.0     │
│ 27  │ false │ svm    │ 132      │ 1.0     │ 132        │ 1.0     │ 1.0     │
│ 28  │ false │ svm    │ 137      │ 1.0     │ 137        │ 1.0     │ 1.0     │
│ 29  │ false │ svm    │ 142      │ 1.0     │ 142        │ 1.0     │ 1.0     │
│ 30  │ false │ svm    │ 147      │ 1.0     │ 147        │ 1.0     │ 1.0     │

In [273]:
sbt, svm = Batch.get_bt_svm(;comb_num=7)
jf = JointEq.joint_firm_constructor(cvm, svm; m=1., load_results_dfs=true)

# Get Optimal Capital Structure
cvm = ModelObj.set_opt_k_struct(cvm, jf.cvmdf)
mu_s = .5
mu_b = cvm.optKS.mu_b
m = cvm.optKS.m
c = cvm.optKS.c
p = cvm.optKS.p
vbl = NaN

jks = JointEq.joint_eq_set_k_struct!(jf; mu_s=mu_s,  
                                     mu_b=mu_b,
                                     m=m, c=c, p=p)

# tmp = JointEq.joint_eq_fd(jf;  mu_s=mu_s,  
#                                     mu_b=mu_b,
#                                     m=m, c=c, p=p)
tmp = JointEq.joint_eq_fd(jf; jks=jks) #, sf_vb=NaN, rf_vb=60.61)

Setting parameter dictionary using unique combination ID...
Batch object exists: true
Loading SVM object...
Unable to load batch object file.
Batch Object is incompatible! Loading surfaces only instead.
Setting initial vbl value to NaN
Setting initial vbh value to NaN
Setting initial c value to NaN
Setting initial p value to NaN
Interpolating Bond Pricing Surfaces...
  0.214708 seconds (811.43 k allocations: 137.112 MiB, 19.28% gc time)
Interpolating bond pricing surfaces...
  0.207777 seconds (811.43 k allocations: 137.112 MiB, 18.04% gc time)
Loading optimal results dataframe...
Setting parameter dictionary using (m, m_comb_num) ID pair...
Loading optimal results dataframe...
Computing Equity Vmax
Vmax: 125.0
phi0: -42.45407878317806
phi1: 0.9999999999999998
pv_rfdebt: 56.39588710415258
debt_abs_per_diff: 4.2137778338190744e-10
eq_abs_per_diff: 0.0008333361964231212
Equity Vmax: 300.8274042113857
 
eq_max: 258.3688800900978
eq_vbl: 0.0
here bpr
Computing Constant Volatility Equity Va

V0: 100.0; equity: 52.34646439063594
Equity Core Function Computation Time: 0.040750980377197266
Total Equity FD Core Function Computation Time: 0.09496879577636719
Total computation time: 0.12721896171569824
Computing Equity Vmax
Vmax: 125.0
phi0: -42.45407878317806
phi1: 0.9999999999999998
pv_rfdebt: 56.39588710415258
debt_abs_per_diff: 4.2137778338190744e-10
eq_abs_per_diff: 0.0008333361964231212
Equity Vmax: 300.8274042113857
 
eq_max: 258.3688800900978
eq_vbl: 0.0
here bpr
Computing Constant Volatility Equity Values
Finished computing Constant Volatility Equity Values
Time to compute Constant Volatility Equity Values: 0.008169889450073242
 
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 52.19892132629879
Equity Core Function Computation Time: 0.04439711570739746
Total Equity FD Core Function Computation Time: 0.09403395652770996
Total computation time: 0.1263740062713623
Computing Equity Vmax
Vmax: 125.0
phi0: -42.45407878317806
phi1: 0.9999999999999

2×31 DataFrame. Omitted printing of 24 columns
│ Row │ mu_s    │ m       │ mu_b    │ c       │ p       │ fi_vb   │ sf_vb   │
│     │ Float64 │ Float64 │ Float64 │ Float64 │ Float64 │ Float64 │ Float64 │
├─────┼─────────┼─────────┼─────────┼─────────┼─────────┼─────────┼─────────┤
│ 1   │ 0.5     │ 1.0     │ 1.0     │ 4.65309 │ 56.3957 │ 59.8191 │ 59.8191 │
│ 2   │ 0.5     │ 1.0     │ 1.0     │ 4.65309 │ 56.3957 │ 61.4767 │ NaN     │

# Optimal Joint VB

In [91]:
modls = ["Batch", "ModelObj", "AnalyticFunctions", 
         "BondPrInterp", "EqFinDiff", "JointEq"]
for modl in modls
    include(string(joinpath(module_path, modl), "/", modl, ".jl"))
end

In [89]:
df = JointEq.find_joint_optimal_vb(jf, jks)

Computing Equity Vmax
Vmax: 125.0
phi0: -42.45407878317806
phi1: 0.9999999999999998
pv_rfdebt: 56.39588710415258
debt_abs_per_diff: NaN
eq_abs_per_diff: NaN
Vmax: 125.0
phi0: -42.45407878317806
phi1: 0.9999999999999998
pv_rfdebt: 56.39588710415258
debt_abs_per_diff: 4.2137778338190744e-10
eq_abs_per_diff: 0.0008333361964231212
Equity Vmax: 300.8274042113857
 
eq_max: 1.7205725065208473
eq_vbl: 0.0
eq_vbl: 0.0
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 56.068180287210325
Equity Core Function Computation Time: 0.17743206024169922
Total Equity FD Core Function Computation Time: 0.2503550052642822
Computing Constant Volatility Equity Values
Finished computing Constant Volatility Equity Values
Time to compute Constant Volatility Equity Values: 0.008258819580078125
 
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 52.84418833592458
Equity Core Function Computation Time: 0.045614004135131836
Total Equity FD Core Function Computa

V0: 100.0; equity: 52.5855169738946
Equity Core Function Computation Time: 0.04342484474182129
Total Equity FD Core Function Computation Time: 0.09325909614562988
Total computation time: 0.22701787948608398
Computing Equity Vmax
Vmax: 125.0
phi0: -42.45407878317806
phi1: 0.9999999999999998
pv_rfdebt: 56.39588710415258
debt_abs_per_diff: NaN
eq_abs_per_diff: NaN
Vmax: 125.0
phi0: -42.45407878317806
phi1: 0.9999999999999998
pv_rfdebt: 56.39588710415258
debt_abs_per_diff: 4.2137778338190744e-10
eq_abs_per_diff: 0.0008333361964231212
Equity Vmax: 300.8274042113857
 
eq_max: 1.6181715054804904
eq_vbl: 0.0
eq_vbl: 0.0
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 55.13858317709927
Equity Core Function Computation Time: 0.08525991439819336
Total Equity FD Core Function Computation Time: 0.13393497467041016
Computing Constant Volatility Equity Values
Finished computing Constant Volatility Equity Values
Time to compute Constant Volatility Equity Values: 0.0082609

V0: 100.0; equity: 54.428169663365345
Equity Core Function Computation Time: 0.045986175537109375
Total Equity FD Core Function Computation Time: 0.08953404426574707
Computing Constant Volatility Equity Values
Finished computing Constant Volatility Equity Values
Time to compute Constant Volatility Equity Values: 0.008231878280639648
 
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 52.75126430982115
Equity Core Function Computation Time: 0.07055282592773438
Total Equity FD Core Function Computation Time: 0.12041091918945312
Total computation time: 0.5559840202331543
Computing Equity Vmax
Vmax: 125.0
phi0: -42.45407878317806
phi1: 0.9999999999999998
pv_rfdebt: 56.39588710415258
debt_abs_per_diff: NaN
eq_abs_per_diff: NaN
Vmax: 125.0
phi0: -42.45407878317806
phi1: 0.9999999999999998
pv_rfdebt: 56.39588710415258
debt_abs_per_diff: 4.2137778338190744e-10
eq_abs_per_diff: 0.0008333361964231212
Equity Vmax: 300.8274042113857
 
eq_max: 1.5477136302341654
eq_vbl: 

debt_abs_per_diff: 4.2137778338190744e-10
eq_abs_per_diff: 0.0008333361964231212
Equity Vmax: 300.8274042113857
 
eq_max: 258.3688800900978
eq_vbl: 0.0
here bpr
Computing Constant Volatility Equity Values
Finished computing Constant Volatility Equity Values
Time to compute Constant Volatility Equity Values: 0.00949406623840332
 
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 66.89872597151336; equity: 4.641594680236235
Equity Core Function Computation Time: 0.04837489128112793
Total Equity FD Core Function Computation Time: 0.09739804267883301
Total computation time: 0.2795131206512451
eq_vbl: 4.641594680236235
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 53.54026476155621
Equity Core Function Computation Time: 0.04510092735290527
Total Equity FD Core Function Computation Time: 0.08940601348876953
Computing Constant Volatility Equity Values
Finished computing Constant Volatility Equity Values
Time to compute Constant Volatility Equity Va

Computing equity values... 
V0: 100.0; equity: 52.71733216935778
Equity Core Function Computation Time: 0.04786109924316406
Total Equity FD Core Function Computation Time: 0.23807907104492188
Total computation time: 0.41042017936706543
Computing Equity Vmax
Vmax: 125.0
phi0: -42.45407878317806
phi1: 0.9999999999999998
pv_rfdebt: 56.39588710415258
debt_abs_per_diff: NaN
eq_abs_per_diff: NaN
Vmax: 125.0
phi0: -42.45407878317806
phi1: 0.9999999999999998
pv_rfdebt: 56.39588710415258
debt_abs_per_diff: 4.2137778338190744e-10
eq_abs_per_diff: 0.0008333361964231212
Equity Vmax: 300.8274042113857
 
eq_max: 1.6553539689718233
eq_vbl: 0.0
eq_vbl: 0.0
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 55.54622860862083
Equity Core Function Computation Time: 0.04291105270385742
Total Equity FD Core Function Computation Time: 0.08080005645751953
Computing Constant Volatility Equity Values
Finished computing Constant Volatility Equity Values
Time to compute Constant Volati

Computing equity values... 
V0: 100.0; equity: 58.78299513821656
Equity Core Function Computation Time: 0.0739748477935791
Total Equity FD Core Function Computation Time: 0.11818099021911621
Computing Constant Volatility Equity Values
Finished computing Constant Volatility Equity Values
Time to compute Constant Volatility Equity Values: 0.008302927017211914
 
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 52.38524861699226
Equity Core Function Computation Time: 0.04863095283508301
Total Equity FD Core Function Computation Time: 0.23812484741210938
Total computation time: 0.4090390205383301
Computing Equity Vmax
Vmax: 125.0
phi0: -42.45407878317806
phi1: 0.9999999999999998
pv_rfdebt: 56.39588710415258
debt_abs_per_diff: NaN
eq_abs_per_diff: NaN
Vmax: 125.0
phi0: -42.45407878317806
phi1: 0.9999999999999998
pv_rfdebt: 56.39588710415258
debt_abs_per_diff: 4.2137778338190744e-10
eq_abs_per_diff: 0.0008333361964231212
Equity Vmax: 300.8274042113857
 
eq_max: 1.

Computing equity values... 
V0: 100.0; equity: 55.17073373928847
Equity Core Function Computation Time: 0.07274389266967773
Total Equity FD Core Function Computation Time: 0.11947298049926758
Computing Constant Volatility Equity Values
Finished computing Constant Volatility Equity Values
Time to compute Constant Volatility Equity Values: 0.009466171264648438
 
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 52.54443176879256
Equity Core Function Computation Time: 0.0480189323425293
Total Equity FD Core Function Computation Time: 0.24277710914611816
Total computation time: 0.41661691665649414
Computing Equity Vmax
Vmax: 125.0
phi0: -42.45407878317806
phi1: 0.9999999999999998
pv_rfdebt: 56.39588710415258
debt_abs_per_diff: NaN
eq_abs_per_diff: NaN
Vmax: 125.0
phi0: -42.45407878317806
phi1: 0.9999999999999998
pv_rfdebt: 56.39588710415258
debt_abs_per_diff: 4.2137778338190744e-10
eq_abs_per_diff: 0.0008333361964231212
Equity Vmax: 300.8274042113857
 
eq_max: 1

2×32 DataFrame. Omitted printing of 27 columns
│ Row │ sf_defaults_first │ fi_vb   │ sf_vb   │ rf_vb   │ vb      │
│     │ Bool              │ Float64 │ Float64 │ Float64 │ Float64 │
├─────┼───────────────────┼─────────┼─────────┼─────────┼─────────┤
│ 1   │ false             │ 59.8191 │ 59.8191 │ NaN     │ 60.5872 │
│ 2   │ false             │ 61.4767 │ NaN     │ 60.5872 │ 60.5872 │

## Misrepresentation

In [308]:
modls = ["Batch", "ModelObj", "AnalyticFunctions", 
         "BondPrInterp", "EqFinDiff", "JointEq"]
for modl in modls
    include(string(joinpath(module_path, modl), "/", modl, ".jl"))
end

In [309]:
JointEq.joint_eq_fd(jf; jks=jks2, rf_vb=56.3954)

Computing Equity Vmax
Vmax: 125.0
phi0: -42.45407878317806
phi1: 0.9999999999999998
pv_rfdebt: 56.39588710415258
debt_abs_per_diff: NaN
eq_abs_per_diff: NaN
Vmax: 125.0
phi0: -42.45407878317806
phi1: 0.9999999999999998
pv_rfdebt: 56.39588710415258
debt_abs_per_diff: 4.2137778338190744e-10
eq_abs_per_diff: 0.0008333361964231212
Equity Vmax: 300.8274042113857
 
eq_max: 1.615211990863021
eq_vbl: 0.0
Computing Equity Vmax
Vmax: 125.0
phi0: -42.45407878317806
phi1: 0.9999999999999998
pv_rfdebt: 56.39588710415258
debt_abs_per_diff: 4.2137778338190744e-10
eq_abs_per_diff: 0.0008333361964231212
Equity Vmax: 300.8274042113857
 
eq_max: 258.3688800900977
eq_vbl: 0.0
here bpr
Computing Constant Volatility Equity Values
Finished computing Constant Volatility Equity Values
Time to compute Constant Volatility Equity Values: 0.07221317291259766
 
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 59.819081667592606; equity: -0.8202560039467778
Equity Core Function Computation Time: 0.0944

2×31 DataFrame. Omitted printing of 24 columns
│ Row │ mu_s    │ m       │ mu_b    │ c       │ p       │ fi_vb   │ sf_vb   │
│     │ Float64 │ Float64 │ Float64 │ Float64 │ Float64 │ Float64 │ Float64 │
├─────┼─────────┼─────────┼─────────┼─────────┼─────────┼─────────┼─────────┤
│ 1   │ 1.0     │ 1.0     │ 1.0     │ 4.65309 │ 56.3957 │ 59.8191 │ 59.8191 │
│ 2   │ 1.0     │ 1.0     │ 1.0     │ 4.65309 │ 56.3957 │ 61.4767 │ NaN     │

In [311]:
jf.cvmdf[1, :]

DataFrameRow. Omitted printing of 29 columns
│ Row │ comb_num │ m       │ m_comb_num │ gross_delta │ delta   │ iota    │
│     │ Int64    │ Float64 │ Int64      │ Float64     │ Float64 │ Float64 │
├─────┼──────────┼─────────┼────────────┼─────────────┼─────────┼─────────┤
│ 1   │ 1        │ 1.0     │ 1          │ 0.02        │ 0.02    │ 0.0     │

In [312]:
EqFinDiff.get_cvm_eq(cvm, 100., cvm.pm.sigmal; 
                     mu_b=cvm.optKS.mu_b, m=1.,
                     c=cvm.optKS.c, p=cvm.optKS.p)

55.41961358518024

In [306]:
cvm.optKS

ModelObj.KStruct
  mu_b: Float64 1.0
  m: Float64 1.0
  c: Float64 4.653090309030903
  p: Float64 56.39566933936072
  vbl: Float64 59.81908166752027


In [307]:
EqFinDiff.get_cvm_eq(cvm, cvm.optKS.vbl, cvm.pm.sigmal; 
                     mu_b=cvm.optKS.mu_b, m=1.,
                     c=cvm.optKS.c, p=cvm.optKS.p)

4.618527782440651e-13

In [305]:


EqFinDiff.eq_fd(cvm; vbl=jks2.vbl, mu_b=jks2.mu_b,
                 m=jks2.m, c=jks2.c, p=jks2.p)

Computing Equity Vmax
Vmax: 125.0
phi0: -42.45407878317806
phi1: 0.9999999999999998
pv_rfdebt: 56.39588710415258
debt_abs_per_diff: NaN
eq_abs_per_diff: NaN
Equity Vmax: 131.25
 
eq_max: 88.33241208906581
eq_vbl: 0.0
here bpr


80773.17971219588

In [310]:
jks2 = deepcopy(jks)
setfield!(jks2, :mu_s, 1.)
df = JointEq.find_joint_optimal_vb(jf, jks2)


Computing Equity Vmax
Vmax: 125.0
phi0: -42.45407878317806
phi1: 0.9999999999999998
pv_rfdebt: 56.39588710415258
debt_abs_per_diff: NaN
eq_abs_per_diff: NaN
Vmax: 125.0
phi0: -42.45407878317806
phi1: 0.9999999999999998
pv_rfdebt: 56.39588710415258
debt_abs_per_diff: 4.2137778338190744e-10
eq_abs_per_diff: 0.0008333361964231212
Equity Vmax: 300.8274042113857
 
eq_max: 1.7205725065208473
eq_vbl: 0.0
eq_vbl: 0.0
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 56.441491158764016
Equity Core Function Computation Time: 0.052459001541137695
Total Equity FD Core Function Computation Time: 0.12990379333496094
Computing Constant Volatility Equity Values
Finished computing Constant Volatility Equity Values
Time to compute Constant Volatility Equity Values: 0.008147954940795898
 
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 52.971185692487204
Equity Core Function Computation Time: 0.1313629150390625
Total Equity FD Core Function Comput

Computing equity values... 
V0: 100.0; equity: 52.69437946845012
Equity Core Function Computation Time: 0.04958009719848633
Total Equity FD Core Function Computation Time: 0.11028099060058594
Total computation time: 0.2778971195220947
Computing Equity Vmax
Vmax: 125.0
phi0: -42.45407878317806
phi1: 0.9999999999999998
pv_rfdebt: 56.39588710415258
debt_abs_per_diff: NaN
eq_abs_per_diff: NaN
Vmax: 125.0
phi0: -42.45407878317806
phi1: 0.9999999999999998
pv_rfdebt: 56.39588710415258
debt_abs_per_diff: 4.2137778338190744e-10
eq_abs_per_diff: 0.0008333361964231212
Equity Vmax: 300.8274042113857
 
eq_max: 1.6181715054804904
eq_vbl: 0.0
eq_vbl: 0.0
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 55.45842791477588
Equity Core Function Computation Time: 0.053708791732788086
Total Equity FD Core Function Computation Time: 0.10593199729919434
Computing Constant Volatility Equity Values
Finished computing Constant Volatility Equity Values
Time to compute Constant Volati

Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 54.52984844031928
Equity Core Function Computation Time: 0.04987287521362305
Total Equity FD Core Function Computation Time: 0.10128593444824219
Computing Constant Volatility Equity Values
Finished computing Constant Volatility Equity Values
Time to compute Constant Volatility Equity Values: 0.011567115783691406
 
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 52.77358579324625
Equity Core Function Computation Time: 0.0529940128326416
Total Equity FD Core Function Computation Time: 0.1096189022064209
Total computation time: 0.439237117767334
Computing Equity Vmax
Vmax: 125.0
phi0: -42.45407878317806
phi1: 0.9999999999999998
pv_rfdebt: 56.39588710415258
debt_abs_per_diff: NaN
eq_abs_per_diff: NaN
Vmax: 125.0
phi0: -42.45407878317806
phi1: 0.9999999999999998
pv_rfdebt: 56.39588710415258
debt_abs_per_diff: 4.2137778338190744e-10
eq_abs_per_diff: 0.0008333361964231212
Equity Vmax: 3

Finished computing Constant Volatility Equity Values
Time to compute Constant Volatility Equity Values: 0.011739969253540039
 
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 66.89872597151336; equity: 4.641594680236235
Equity Core Function Computation Time: 0.05271100997924805
Total Equity FD Core Function Computation Time: 0.11169791221618652
Total computation time: 0.16731905937194824
eq_vbl: 4.641594680236235
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 53.27654274968232
Equity Core Function Computation Time: 0.29245901107788086
Total Equity FD Core Function Computation Time: 0.3758718967437744
Computing Constant Volatility Equity Values
Finished computing Constant Volatility Equity Values
Time to compute Constant Volatility Equity Values: 0.011523962020874023
 
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 53.54939399220763
Equity Core Function Computation Time: 0.048850059509277344
Total Equity FD Cor

Computing equity values... 
V0: 100.0; equity: 55.88971783831359
Equity Core Function Computation Time: 0.049262046813964844
Total Equity FD Core Function Computation Time: 0.09296607971191406
Computing Constant Volatility Equity Values
Finished computing Constant Volatility Equity Values
Time to compute Constant Volatility Equity Values: 0.011535882949829102
 
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 52.79188996748264
Equity Core Function Computation Time: 0.050065040588378906
Total Equity FD Core Function Computation Time: 0.11079096794128418
Total computation time: 0.27838993072509766
Computing Equity Vmax
Vmax: 125.0
phi0: -42.45407878317806
phi1: 0.9999999999999998
pv_rfdebt: 56.39588710415258
debt_abs_per_diff: NaN
eq_abs_per_diff: NaN
Vmax: 125.0
phi0: -42.45407878317806
phi1: 0.9999999999999998
pv_rfdebt: 56.39588710415258
debt_abs_per_diff: 4.2137778338190744e-10
eq_abs_per_diff: 0.0008333361964231212
Equity Vmax: 300.8274042113857
 
eq_max

V0: 100.0; equity: 52.618124454700585
Equity Core Function Computation Time: 0.25609707832336426
Total Equity FD Core Function Computation Time: 0.3460578918457031
Total computation time: 0.6199178695678711
Computing Equity Vmax
Vmax: 125.0
phi0: -42.45407878317806
phi1: 0.9999999999999998
pv_rfdebt: 56.39588710415258
debt_abs_per_diff: NaN
eq_abs_per_diff: NaN
Vmax: 125.0
phi0: -42.45407878317806
phi1: 0.9999999999999998
pv_rfdebt: 56.39588710415258
debt_abs_per_diff: 4.2137778338190744e-10
eq_abs_per_diff: 0.0008333361964231212
Equity Vmax: 300.8274042113857
 
eq_max: 1.5706523908828514
Computing Equity Vmax
Vmax: 125.0
phi0: -42.45407878317806
phi1: 0.9999999999999998
pv_rfdebt: 56.39588710415258
debt_abs_per_diff: NaN
eq_abs_per_diff: NaN
Equity Vmax: 131.25
 
eq_max: 88.33241208906581
eq_vbl: 0.0
46.610093629763085
here bpr
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 62.54487514795335; equity: 1.6838278139645684
Equity Core Function Computation Time: 0.049777984

Computing equity values... 
V0: 66.17308416758668; equity: 6.963390532750838
Equity Core Function Computation Time: 0.04943203926086426
Total Equity FD Core Function Computation Time: 0.09937000274658203
Total computation time: 0.10830998420715332
eq_vbl: 6.963390532750838
eq_vbl: 0.0
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 64.57112352941479
Equity Core Function Computation Time: 0.05325913429260254
Total Equity FD Core Function Computation Time: 0.09940910339355469
Computing Constant Volatility Equity Values
Finished computing Constant Volatility Equity Values
Time to compute Constant Volatility Equity Values: 0.011636972427368164
 
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 52.40658465941227
Equity Core Function Computation Time: 0.2560920715332031
Total Equity FD Core Function Computation Time: 0.34720396995544434
Total computation time: 0.6233241558074951
Computing Equity Vmax
Vmax: 125.0
phi0: -42.45407878317

V0: 60.573250368346606; equity: 0.15095528766550154
Equity Core Function Computation Time: 0.048462867736816406
Total Equity FD Core Function Computation Time: 0.09861397743225098
Total computation time: 0.10750293731689453
eq_vbl: 0.15095528766550154
eq_vbl: 0.0
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 56.51885484665751
Equity Core Function Computation Time: 0.05168581008911133
Total Equity FD Core Function Computation Time: 0.09725594520568848
Computing Constant Volatility Equity Values
Finished computing Constant Volatility Equity Values
Time to compute Constant Volatility Equity Values: 0.011570930480957031
 
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 52.627217206881085
Equity Core Function Computation Time: 0.04873204231262207
Total Equity FD Core Function Computation Time: 0.10872697830200195
Total computation time: 0.3805510997772217


4×32 DataFrame. Omitted printing of 27 columns
│ Row │ sf_defaults_first │ fi_vb   │ sf_vb   │ rf_vb   │ vb      │
│     │ Bool              │ Float64 │ Float64 │ Float64 │ Float64 │
├─────┼───────────────────┼─────────┼─────────┼─────────┼─────────┤
│ 1   │ true              │ 59.8191 │ 64.1349 │ NaN     │ 64.1349 │
│ 2   │ true              │ 61.4767 │ NaN     │ 61.4767 │ 64.1349 │
│ 3   │ false             │ 59.8191 │ 59.8191 │ NaN     │ 60.5733 │
│ 4   │ false             │ 61.4767 │ NaN     │ 60.5733 │ 60.5733 │

# Optimal mu_b

In [119]:
modls = ["Batch", "ModelObj", "AnalyticFunctions", 
         "BondPrInterp", "EqFinDiff", "JointEq"]
for modl in modls
    include(string(joinpath(module_path, modl), "/", modl, ".jl"))
end

In [232]:
sbt, svm = Batch.get_bt_svm(;comb_num=7)
svm = ModelObj.set_opt_k_struct(svm, jf.svmdf)
svm.optKS

Setting parameter dictionary using unique combination ID...
Batch object exists: true
Loading SVM object...
Unable to load batch object file.
Batch Object is incompatible! Loading surfaces only instead.
Setting initial vbl value to NaN
Setting initial vbh value to NaN
Setting initial c value to NaN
Setting initial p value to NaN
Interpolating Bond Pricing Surfaces...
  0.208735 seconds (811.42 k allocations: 137.112 MiB, 18.32% gc time)
Interpolating bond pricing surfaces...
  0.370391 seconds (811.43 k allocations: 137.113 MiB, 51.26% gc time)


ModelObj.KStruct
  mu_b: Float64 1.0
  m: Float64 1.0
  c: Float64 4.0861086108610865
  p: Float64 49.49377589822867
  vbl: Float64 53.95006773115467


In [109]:
sbt, svm = Batch.get_bt_svm(;comb_num=7)
jf = JointEq.joint_firm_constructor(cvm, svm; m=1., load_results_dfs=true)

# Get Optimal Capital Structure
cvm = ModelObj.set_opt_k_struct(cvm, jf.cvmdf)
mu_s = .5



mu_b = cvm.optKS.mu_b

x = 10.
m = cvm.optKS.m
c = cvm.optKS.c/x
p = cvm.optKS.p/x

vbl = NaN

jks = JointEq.joint_eq_set_k_struct!(jf; mu_s=mu_s,  
                                     mu_b=mu_b,
                                     m=m, c=c, p=p)

Setting parameter dictionary using unique combination ID...
Batch object exists: true
Loading SVM object...
Unable to load batch object file.
Batch Object is incompatible! Loading surfaces only instead.
Setting initial vbl value to NaN
Setting initial vbh value to NaN
Setting initial c value to NaN
Setting initial p value to NaN
Interpolating Bond Pricing Surfaces...
  0.267117 seconds (811.43 k allocations: 137.113 MiB, 15.38% gc time)
Interpolating bond pricing surfaces...
  0.243517 seconds (811.43 k allocations: 137.113 MiB, 16.44% gc time)
Loading optimal results dataframe...
Setting parameter dictionary using (m, m_comb_num) ID pair...
Loading optimal results dataframe...
Computing Equity Vmax
Vmax: 125.0
phi0: -4.245407878317797
phi1: 0.9999999999999998
pv_rfdebt: 5.639588710415258
debt_abs_per_diff: 0.000556384381953215
eq_abs_per_diff: 2.729794729589071e-7
Equity Vmax: 193.91602699731453
 
eq_max: 189.67061910600253
eq_vbl: 0.0
here bpr
Computing Constant Volatility Equity Val

Computing equity values... 
V0: 100.0; equity: 95.75433696715858
Equity Core Function Computation Time: 0.04291701316833496
Total Equity FD Core Function Computation Time: 0.26224517822265625
Total computation time: 0.28133392333984375
Computing Equity Vmax
Vmax: 125.0
phi0: -4.245407878317797
phi1: 0.9999999999999998
pv_rfdebt: 5.639588710415258
debt_abs_per_diff: 0.000556384381953215
eq_abs_per_diff: 2.729794729589071e-7
Equity Vmax: 193.91602699731453
 
eq_max: 189.67061910600242
eq_vbl: 0.0
here bpr
Computing Constant Volatility Equity Values
Finished computing Constant Volatility Equity Values
Time to compute Constant Volatility Equity Values: 0.008275032043457031
 
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 95.7543367045214
Equity Core Function Computation Time: 0.046716928482055664
Total Equity FD Core Function Computation Time: 0.096588134765625
Total computation time: 0.1158440113067627
Computing Equity Vmax
Vmax: 125.0
phi0: -4.2454078783177

Main.JointEq.JointKStruct(0.5, 1.0, 1.0, 0.4653090309030903, 5.639566933936072, 6.14868951742782, 5.9819081667592595, 5.9819081667592595, 6.14868951742782, 6.14868951742782)

In [262]:
modls = ["Batch", "ModelObj", "AnalyticFunctions", 
         "BondPrInterp", "EqFinDiff", "JointEq"]
for modl in modls
    include(string(joinpath(module_path, modl), "/", modl, ".jl"))
end

In [272]:
x = 9
jks3 = deepcopy(jks)
jks3.m = cvm.optKS.m
jks3.c = cvm.optKS.c/x
jks3.p = cvm.optKS.p/x

df = JointEq.find_optimal_bond_measure(cvm; jks=jks3)

Computing Equity Vmax
Vmax: 125.0
phi0: -2.358559932398779
phi1: 0.9999999999999998
pv_rfdebt: 3.133104839119588
debt_abs_per_diff: NaN
eq_abs_per_diff: NaN
Equity Vmax: 131.25
 
eq_max: 128.8914400652133
eq_vbl: 0.0
5.178899292195899
here bpr
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 97.64145930254111
Equity Core Function Computation Time: 0.04192709922790527
Total Equity FD Core Function Computation Time: 0.08401608467102051
Total computation time: 0.09011197090148926
Computing Equity Vmax
Vmax: 125.0
phi0: -5.958467197639021
phi1: 0.9999999999999998
pv_rfdebt: 7.915212225144222
debt_abs_per_diff: NaN
eq_abs_per_diff: NaN
Equity Vmax: 131.25
 
eq_max: 125.29153171725751
eq_vbl: 0.0
5.178899292195899
here bpr
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 94.04153858624045
Equity Core Function Computation Time: 0.040740966796875
Total Equity FD Core Function Computation Time: 0.08663392066955566
Total computation time:

Computing equity values... 
V0: 100.0; equity: 21.421132740553414
Equity Core Function Computation Time: 0.04392600059509277
Total Equity FD Core Function Computation Time: 0.08450794219970703
Total computation time: 0.09041213989257812
Computing Equity Vmax
Vmax: 125.0
phi0: -63.55698344148289
phi1: 0.9999999999999998
pv_rfdebt: 84.42893040153837
debt_abs_per_diff: NaN
eq_abs_per_diff: NaN
Equity Vmax: 131.25
 
eq_max: 61.06325580543533
eq_vbl: 0.0
5.178899292195899
here bpr
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 12.021718318165403
Equity Core Function Computation Time: 0.19043302536010742
Total Equity FD Core Function Computation Time: 0.27321600914001465
Total computation time: 0.27909398078918457
Computing Equity Vmax
Vmax: 125.0
phi0: -67.15689070672313
phi1: 0.9999999999999998
pv_rfdebt: 89.211037787563
debt_abs_per_diff: NaN
eq_abs_per_diff: NaN
Equity Vmax: 131.25
 
eq_max: 54.61647104847854
eq_vbl: 0.0
5.178899292195899
here bpr
Shape of 

1×27 DataFrame. Omitted printing of 21 columns
│ Row │ ROE     │ V0      │ alpha   │ c       │ debt    │ delta   │
│     │ Float64 │ Float64 │ Float64 │ Float64 │ Float64 │ Float64 │
├─────┼─────────┼─────────┼─────────┼─────────┼─────────┼─────────┤
│ 1   │ 27.0543 │ 100.0   │ 0.6     │ 0.51701 │ 56.3281 │ 0.02    │

In [263]:
x = 10.
jks3 = deepcopy(jks)
jks3.m = svm.optKS.m
jks3.c = svm.optKS.c/x
jks3.p = svm.optKS.p/x

df = JointEq.find_optimal_bond_measure(svm; jks=jks3)

Computing Equity Vmax
Vmax: 125.0
phi0: -1.8625640430196766
phi1: 0.9999999999999998
pv_rfdebt: 2.4747586628872567
debt_abs_per_diff: 0.0004659660055879428
eq_abs_per_diff: 6.690468735152632e-9
Equity Vmax: 203.61182834718028
 
eq_max: 201.74926430411764
eq_vbl: 0.0
here bpr
Computing Constant Volatility Equity Values
Finished computing Constant Volatility Equity Values
Time to compute Constant Volatility Equity Values: 0.0727078914642334
 
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 98.137459225096
Equity Core Function Computation Time: 0.06720495223999023
Total Equity FD Core Function Computation Time: 0.25765514373779297
Total computation time: 0.8071959018707275
Computing Equity Vmax
Vmax: 125.0
phi0: -1.8625640430196766
phi1: 0.9999999999999998
pv_rfdebt: 2.4747586628872567
debt_abs_per_diff: 0.0004659660055879428
eq_abs_per_diff: 6.690468735152632e-9
Equity Vmax: 203.61182834718028
 
eq_max: 201.74926430411764
eq_vbl: 0.0
here bpr
Computing Const

Computing equity values... 
V0: 100.0; equity: 98.1374537453297
Equity Core Function Computation Time: 0.19417715072631836
Total Equity FD Core Function Computation Time: 0.27616310119628906
Total computation time: 0.2964658737182617
Computing Equity Vmax
Vmax: 125.0
phi0: -1.8625640430196766
phi1: 0.9999999999999998
pv_rfdebt: 2.4747586628872567
debt_abs_per_diff: 0.0004659660055879428
eq_abs_per_diff: 6.690468735152632e-9
Equity Vmax: 203.61182834718028
 
eq_max: 201.74926430411764
eq_vbl: 0.0
here bpr
Computing Constant Volatility Equity Values
Finished computing Constant Volatility Equity Values
Time to compute Constant Volatility Equity Values: 0.008305072784423828
 
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 98.1374533654381
Equity Core Function Computation Time: 0.04288601875305176
Total Equity FD Core Function Computation Time: 0.09318017959594727
Total computation time: 0.1133720874786377
Computing Equity Vmax
Vmax: 125.0
phi0: -1.86256404301

Computing equity values... 
V0: 100.0; equity: 95.29416950204974
Equity Core Function Computation Time: 0.1936178207397461
Total Equity FD Core Function Computation Time: 0.27539515495300293
Total computation time: 0.29447293281555176
Computing Equity Vmax
Vmax: 125.0
phi0: -4.7054249507865515
phi1: 0.9999999999999998
pv_rfdebt: 6.252021885188858
debt_abs_per_diff: 0.0004962315658432691
eq_abs_per_diff: 4.235045104883471e-7
Equity Vmax: 193.91602699731453
 
eq_max: 189.21060202086622
eq_vbl: 0.0
here bpr
Computing Constant Volatility Equity Values
Finished computing Constant Volatility Equity Values
Time to compute Constant Volatility Equity Values: 0.008267879486083984
 
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 95.29416914105305
Equity Core Function Computation Time: 0.04318594932556152
Total Equity FD Core Function Computation Time: 0.09354186058044434
Total computation time: 0.11272478103637695
Computing Equity Vmax
Vmax: 125.0
phi0: -4.705424950

Computing equity values... 
V0: 100.0; equity: 92.44861903846032
Equity Core Function Computation Time: 0.19623804092407227
Total Equity FD Core Function Computation Time: 0.2896139621734619
Total computation time: 0.30744385719299316
Computing Equity Vmax
Vmax: 125.0
phi0: -7.548285858553426
phi1: 0.9999999999999998
pv_rfdebt: 10.02928510749046
debt_abs_per_diff: 0.0007870419225102976
eq_abs_per_diff: 3.922141377718338e-6
Equity Vmax: 184.6819304736329
 
eq_max: 177.13364385093
eq_vbl: 0.0
here bpr
Computing Constant Volatility Equity Values
Finished computing Constant Volatility Equity Values
Time to compute Constant Volatility Equity Values: 0.008224010467529297
 
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 92.44861760056497
Equity Core Function Computation Time: 0.0426480770111084
Total Equity FD Core Function Computation Time: 0.09305810928344727
Total computation time: 0.11095881462097168
Computing Equity Vmax
Vmax: 125.0
phi0: -7.548285858553426

Computing equity values... 
V0: 100.0; equity: 89.59682413974275
Equity Core Function Computation Time: 0.19350719451904297
Total Equity FD Core Function Computation Time: 0.2749040126800537
Total computation time: 0.2928159236907959
Computing Equity Vmax
Vmax: 125.0
phi0: -10.3911467663203
phi1: 0.9999999999999998
pv_rfdebt: 13.806548329792063
debt_abs_per_diff: 0.0005285051718083283
eq_abs_per_diff: 1.5437616561687713e-5
Equity Vmax: 184.6819304736329
 
eq_max: 174.29077740184232
eq_vbl: 0.0
here bpr
Computing Constant Volatility Equity Values
Finished computing Constant Volatility Equity Values
Time to compute Constant Volatility Equity Values: 0.008302927017211914
 
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 89.59681572555652
Equity Core Function Computation Time: 0.04262495040893555
Total Equity FD Core Function Computation Time: 0.09323382377624512
Total computation time: 0.1110830307006836
Computing Equity Vmax
Vmax: 125.0
phi0: -10.39114676632

...

V0: 100.0; equity: 34.48177533894579
Equity Core Function Computation Time: 0.04705405235290527
Total Equity FD Core Function Computation Time: 0.09785795211791992
Total computation time: 0.1421520709991455
Computing Equity Vmax
Vmax: 125.0
phi0: -53.03406038282342
phi1: 0.9999999999999998
pv_rfdebt: 70.46549666431609
debt_abs_per_diff: 2.7847887908331484e-9
eq_abs_per_diff: 0.0009408685032500163
Equity Vmax: 365.65758999021574
 
eq_max: 312.6170488767632
eq_vbl: 0.0
here bpr
Computing Constant Volatility Equity Values
Finished computing Constant Volatility Equity Values
Time to compute Constant Volatility Equity Values: 0.008185863494873047
 
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 33.726658130062596
Equity Core Function Computation Time: 0.04657912254333496
Total Equity FD Core Function Computation Time: 0.09627389907836914
Total computation time: 0.14033102989196777
Computing Equity Vmax
Vmax: 125.0
phi0: -53.03406038282342
phi1: 0.9999999999999

V0: 100.0; equity: 30.892447760926377
Equity Core Function Computation Time: 0.04663991928100586
Total Equity FD Core Function Computation Time: 0.096282958984375
Total computation time: 0.1418168544769287
Computing Equity Vmax
Vmax: 125.0
phi0: -55.876921290590296
phi1: 0.9999999999999998
pv_rfdebt: 74.2427598866177
debt_abs_per_diff: 2.784899733293371e-9
eq_abs_per_diff: 0.0009551826330408062
Equity Vmax: 383.9404694897265
 
eq_max: 328.05658770863545
eq_vbl: 0.0
here bpr
Computing Constant Volatility Equity Values
Finished computing Constant Volatility Equity Values
Time to compute Constant Volatility Equity Values: 0.008143901824951172
 
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 30.23210070298719
Equity Core Function Computation Time: 0.0467219352722168
Total Equity FD Core Function Computation Time: 0.09637188911437988
Total computation time: 0.14208102226257324
Computing Equity Vmax
Vmax: 125.0
phi0: -55.876921290590296
phi1: 0.9999999999999998

V0: 100.0; equity: 4.1592760280566345
Equity Core Function Computation Time: 0.04694199562072754
Total Equity FD Core Function Computation Time: 0.09666800498962402
Total computation time: 0.1424551010131836
  2.135635 seconds (1.12 M allocations: 2.331 GiB, 21.34% gc time)
Computing Equity Vmax
Vmax: 125.0
phi0: -1.8625640430196766
phi1: 0.9999999999999998
pv_rfdebt: 2.4747586628872567
debt_abs_per_diff: 0.0004659660055879428
eq_abs_per_diff: 6.690468735152632e-9
Equity Vmax: 203.61182834718028
 
eq_max: 201.74926430411784
eq_vbl: 0.0
here bpr
Computing Constant Volatility Equity Values
Finished computing Constant Volatility Equity Values
Time to compute Constant Volatility Equity Values: 0.00823211669921875
 
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 98.13745907182829
Equity Core Function Computation Time: 0.04701709747314453
Total Equity FD Core Function Computation Time: 0.1114799976348877
Total computation time: 0.13161206245422363
Computing Equ

V0: 100.0; equity: 64.99088101315698
Equity Core Function Computation Time: 0.04706215858459473
Total Equity FD Core Function Computation Time: 0.09810805320739746
Total computation time: 0.12387800216674805
Computing Equity Vmax
Vmax: 125.0
phi0: -35.976894936222166
phi1: 0.9999999999999998
pv_rfdebt: 47.80191733050648
debt_abs_per_diff: 4.6953824774973434e-8
eq_abs_per_diff: 0.0009503001738456388
Equity Vmax: 247.4914499299248
 
eq_max: 211.51010252179884
eq_vbl: 0.0
here bpr
Computing Constant Volatility Equity Values
Finished computing Constant Volatility Equity Values
Time to compute Constant Volatility Equity Values: 0.008172988891601562
 
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 61.42902280748044
Equity Core Function Computation Time: 0.050115108489990234
Total Equity FD Core Function Computation Time: 0.1053769588470459
Total computation time: 0.13234210014343262
Computing Equity Vmax
Vmax: 125.0
phi0: -38.81975584398904
phi1: 0.999999999999

1×27 DataFrame. Omitted printing of 21 columns
│ Row │ ROE     │ V0      │ alpha   │ c        │ debt    │ delta   │
│     │ Float64 │ Float64 │ Float64 │ Float64  │ Float64 │ Float64 │
├─────┼─────────┼─────────┼─────────┼──────────┼─────────┼─────────┤
│ 1   │ 18.2018 │ 100.0   │ 0.6     │ 0.408611 │ 49.189  │ 0.02    │

In [7]:
modls = ["Batch", "ModelObj", "AnalyticFunctions", 
         "BondPrInterp", "EqFinDiff", "JointEq"]
for modl in modls
    include(string(joinpath(module_path, modl), "/", modl, ".jl"))
end

In [ ]:
jf.svmdf[abs.(jf.svmdf[:kappa] .- comb_num) .< 1e-6, :mu_b][1]
# svm.m = jf.svmdf[abs.(jf.svmdf[:comb_num] .- comb_num) .< 1e-6, :m][1]
# svm.c = jf.svmdf[abs.(jf.svmdf[:comb_num] .- comb_num) .< 1e-6, :c][1]
# svm.p = jf.svmdf[abs.(jf.svmdf[:comb_num] .- comb_num) .< 1e-6, :p][1]
# vbl = jf.svmdf[abs.(jf.svmdf[:comb_num] .- comb_num) .< 1e-6, :vb][1]

In [3]:
comb_num = 1
svm.mu_b = jf.svmdf[abs.(jf.svmdf[:comb_num] .- comb_num) .< 1e-6, :mu_b][1]
svm.m = jf.svmdf[abs.(jf.svmdf[:comb_num] .- comb_num) .< 1e-6, :m][1]
svm.c = jf.svmdf[abs.(jf.svmdf[:comb_num] .- comb_num) .< 1e-6, :c][1]
svm.p = jf.svmdf[abs.(jf.svmdf[:comb_num] .- comb_num) .< 1e-6, :p][1]
vbl = jf.svmdf[abs.(jf.svmdf[:comb_num] .- comb_num) .< 1e-6, :vb][1]

UndefVarError: UndefVarError: jf not defined

In [ ]:
modls = ["AnalyticFunctions", "ModelObj",
         "BondPrInterp", "Batch",  "EqFinDiff", "JointEq"]
for modl in modls
    include(string(joinpath(module_path, modl), "/", modl, ".jl"))
end

# Combinations

In [ ]:
bt = Batch.BatchObj()
bt.bp.df

In [ ]:
case = 1
if case == 1
    m = 1.
    m_comb_num = 30
    comb_num = 0
elseif case == 2
    m = NaN
    m_comb_num = 0
    comb_num = 146
elseif case == 3
    m = 1.
    m_comb_num = 30
    comb_num = 146
elseif case == 4
    m = NaN
    m_comb_num = 30
    comb_num = 0
end
bt = Batch.set_par_dict(bt; comb_num=comb_num, m=m, m_comb_num=m_comb_num)

bt.mi._svm_dict

In [ ]:
Batch.get_batch_comb_num(bt; )

# Get Batch & Model Objects

In [ ]:
bt = Batch.get_bt(m=1., m_comb_num=30, display_msgs=false)

In [ ]:
bt = Batch.set_par_dict(bt; m=1., m_comb_num=30, display_msgs=false)

In [ ]:
# Set Directories & Paths (Main, Batch, Maturity, Combination)
bt = Batch.set_comb_res_paths(bt)

In [ ]:
bt, svm = Batch.get_bt_svm(; m=1., m_comb_num=30)

# Process CVM Results

In [136]:
modls = ["Batch", "ModelObj", "AnalyticFunctions", 
         "BondPrInterp", "EqFinDiff"]
for modl in modls
    include(string(joinpath(module_path, modl), "/", modl, ".jl"))
end

In [137]:
bt, cvm = Batch.get_bt_cvm(;  m=1., m_comb_num=31)

Setting parameter dictionary using (m, m_comb_num) ID pair...
Setting initial vbl value to NaN
Setting initial vbh value to NaN
Setting initial c value to NaN
Setting initial p value to NaN
Constant Volatility Model: setting vbh to vbl, lambda to NaN


(Main.Batch.BatchStruct
  model: String "cvm"
  dfn: Main.Batch.DirFileNames
  dfc: Main.Batch.BatchDFColumns
  mi: Main.Batch.ModelInputs
  bp: Main.Batch.BatchParams
  coupon_grid: Array{Float64}((26,)) [0.25, 0.5, 1.0, 1.5, 2.0, 2.5, 3.0, 3.5, 4.0, 4.5  …  8.0, 8.5, 9.0, 9.5, 10.0, 10.5, 11.0, 11.5, 12.0, 12.5]
  pvb_tol_vec: Array{Float64}((0,)) Float64[]
, ModelObj.Firm
  mu_b: Float64 1.0
  m: Float64 1.0
  c: Float64 NaN
  p: Float64 NaN
  vbl: Float64 NaN
  vbh: Float64 NaN
  pm: ModelObj.FirmParams
  model: String "cvm"
  bi: ModelObj.BPrInputs
  bs: ModelObj.BPrSurfs
  bf: ModelObj.BPrInterpFuns
  bit: ModelObj.BPrFixedTTMInputs
  bft: ModelObj.BPrInterpFuns
  optKS: ModelObj.KStruct
)

In [70]:
Batch.optimal_cvm_capital_struct(bt, cvm; firm_obj_fun=:firm_value, replace_optdf=true)

Setting parameter dictionary to batch object's parameter dictionary


1×36 DataFrame. Omitted printing of 30 columns
│ Row │ comb_num │ m       │ m_comb_num │ obj_fun    │ gross_delta │ delta   │
│     │ Int64    │ Float64 │ Int64      │ String     │ Float64     │ Float64 │
├─────┼──────────┼─────────┼────────────┼────────────┼─────────────┼─────────┤
│ 1   │ 146      │ 1.0     │ 146        │ firm_value │ 0.02        │ 0.01925 │

# Process SVM Results

In [9]:
modls = ["Batch", "ModelObj", "AnalyticFunctions", 
         "BondPrInterp", "EqFinDiff"]
for modl in modls
    include(string(joinpath(module_path, modl), "/", modl, ".jl"))
end

In [49]:
plot_script_path = string(main_path, "/Julia/Batch/")
plot_script_name = "diag_compilation.jl"
cvm_res = include(string(plot_script_path, "/", plot_script_name))

Setting initial vbl value to NaN
Setting initial vbh value to NaN
Setting initial c value to NaN
Setting initial p value to NaN
Constant Volatility Model: setting vbh to vbl, lambda to NaN
Setting parameter dictionary to batch object's parameter dictionary
Match found! Replacing row...
Setting initial vbl value to NaN
Setting initial vbh value to NaN
Setting initial c value to NaN
Setting initial p value to NaN
Constant Volatility Model: setting vbh to vbl, lambda to NaN
Setting parameter dictionary to batch object's parameter dictionary
Match found! Replacing row...
Setting initial vbl value to NaN
Setting initial vbh value to NaN
Setting initial c value to NaN
Setting initial p value to NaN
Constant Volatility Model: setting vbh to vbl, lambda to NaN
Setting parameter dictionary to batch object's parameter dictionary
Match found! Replacing row...
Setting initial vbl value to NaN
Setting initial vbh value to NaN
Setting initial c value to NaN
Setting initial p value to NaN
Constant Vo

Setting initial vbl value to NaN
Setting initial vbh value to NaN
Setting initial c value to NaN
Setting initial p value to NaN
Constant Volatility Model: setting vbh to vbl, lambda to NaN
Setting parameter dictionary to batch object's parameter dictionary
Match found! Replacing row...
Setting initial vbl value to NaN
Setting initial vbh value to NaN
Setting initial c value to NaN
Setting initial p value to NaN
Constant Volatility Model: setting vbh to vbl, lambda to NaN
Setting parameter dictionary to batch object's parameter dictionary
Match found! Replacing row...
Setting initial vbl value to NaN
Setting initial vbh value to NaN
Setting initial c value to NaN
Setting initial p value to NaN
Constant Volatility Model: setting vbh to vbl, lambda to NaN
Setting parameter dictionary to batch object's parameter dictionary
Match found! Replacing row...
Setting initial vbl value to NaN
Setting initial vbh value to NaN
Setting initial c value to NaN
Setting initial p value to NaN
Constant Vo

Match found! Replacing row...
Setting initial vbl value to NaN
Setting initial vbh value to NaN
Setting initial c value to NaN
Setting initial p value to NaN
Constant Volatility Model: setting vbh to vbl, lambda to NaN
Setting parameter dictionary to batch object's parameter dictionary
Match found! Replacing row...
Setting initial vbl value to NaN
Setting initial vbh value to NaN
Setting initial c value to NaN
Setting initial p value to NaN
Constant Volatility Model: setting vbh to vbl, lambda to NaN
Setting parameter dictionary to batch object's parameter dictionary
Match found! Replacing row...
Setting initial vbl value to NaN
Setting initial vbh value to NaN
Setting initial c value to NaN
Setting initial p value to NaN
Constant Volatility Model: setting vbh to vbl, lambda to NaN
Setting parameter dictionary to batch object's parameter dictionary
Match found! Replacing row...
Setting initial vbl value to NaN
Setting initial vbh value to NaN
Setting initial c value to NaN
Setting init

Setting initial vbl value to NaN
Setting initial vbh value to NaN
Setting initial c value to NaN
Setting initial p value to NaN
Constant Volatility Model: setting vbh to vbl, lambda to NaN
Setting parameter dictionary to batch object's parameter dictionary
Match found! Replacing row...
Setting initial vbl value to NaN
Setting initial vbh value to NaN
Setting initial c value to NaN
Setting initial p value to NaN
Constant Volatility Model: setting vbh to vbl, lambda to NaN
Setting parameter dictionary to batch object's parameter dictionary
Match found! Replacing row...
Setting initial vbl value to NaN
Setting initial vbh value to NaN
Setting initial c value to NaN
Setting initial p value to NaN
Constant Volatility Model: setting vbh to vbl, lambda to NaN
Setting parameter dictionary to batch object's parameter dictionary
Match found! Replacing row...
Setting initial vbl value to NaN
Setting initial vbh value to NaN
Setting initial c value to NaN
Setting initial p value to NaN
Constant Vo

Setting parameter dictionary to batch object's parameter dictionary
Match found! Replacing row...
Setting initial vbl value to NaN
Setting initial vbh value to NaN
Setting initial c value to NaN
Setting initial p value to NaN
Constant Volatility Model: setting vbh to vbl, lambda to NaN
Setting parameter dictionary to batch object's parameter dictionary
Match found! Replacing row...
Setting initial vbl value to NaN
Setting initial vbh value to NaN
Setting initial c value to NaN
Setting initial p value to NaN
Constant Volatility Model: setting vbh to vbl, lambda to NaN
Setting parameter dictionary to batch object's parameter dictionary
Match found! Replacing row...
Setting initial vbl value to NaN
Setting initial vbh value to NaN
Setting initial c value to NaN
Setting initial p value to NaN
Constant Volatility Model: setting vbh to vbl, lambda to NaN
Setting parameter dictionary to batch object's parameter dictionary
Match found! Replacing row...
Setting initial vbl value to NaN
Setting 

...

Setting parameter dictionary to batch object's parameter dictionary
Match found! Replacing row...
Setting initial vbl value to NaN
Setting initial vbh value to NaN
Setting initial c value to NaN
Setting initial p value to NaN
Constant Volatility Model: setting vbh to vbl, lambda to NaN
Setting parameter dictionary to batch object's parameter dictionary
Match found! Replacing row...
Setting initial vbl value to NaN
Setting initial vbh value to NaN
Setting initial c value to NaN
Setting initial p value to NaN
Constant Volatility Model: setting vbh to vbl, lambda to NaN
Setting parameter dictionary to batch object's parameter dictionary
Match found! Replacing row...
Setting initial vbl value to NaN
Setting initial vbh value to NaN
Setting initial c value to NaN
Setting initial p value to NaN
Constant Volatility Model: setting vbh to vbl, lambda to NaN
Setting parameter dictionary to batch object's parameter dictionary
Match found! Replacing row...
Setting initial vbl value to NaN
Setting 

Setting initial vbl value to NaN
Setting initial vbh value to NaN
Setting initial c value to NaN
Setting initial p value to NaN
Constant Volatility Model: setting vbh to vbl, lambda to NaN
Setting parameter dictionary to batch object's parameter dictionary
Match found! Replacing row...
Setting initial vbl value to NaN
Setting initial vbh value to NaN
Setting initial c value to NaN
Setting initial p value to NaN
Constant Volatility Model: setting vbh to vbl, lambda to NaN
Setting parameter dictionary to batch object's parameter dictionary
Match found! Replacing row...
Setting initial vbl value to NaN
Setting initial vbh value to NaN
Setting initial c value to NaN
Setting initial p value to NaN
Constant Volatility Model: setting vbh to vbl, lambda to NaN
Setting parameter dictionary to batch object's parameter dictionary
Match found! Replacing row...
Setting initial vbl value to NaN
Setting initial vbh value to NaN
Setting initial c value to NaN
Setting initial p value to NaN
Constant Vo

Setting initial vbl value to NaN
Setting initial vbh value to NaN
Setting initial c value to NaN
Setting initial p value to NaN
Constant Volatility Model: setting vbh to vbl, lambda to NaN
Setting parameter dictionary to batch object's parameter dictionary
Match found! Replacing row...
Setting initial vbl value to NaN
Setting initial vbh value to NaN
Setting initial c value to NaN
Setting initial p value to NaN
Constant Volatility Model: setting vbh to vbl, lambda to NaN
Setting parameter dictionary to batch object's parameter dictionary
Match found! Replacing row...
Setting initial vbl value to NaN
Setting initial vbh value to NaN
Setting initial c value to NaN
Setting initial p value to NaN
Constant Volatility Model: setting vbh to vbl, lambda to NaN
Setting parameter dictionary to batch object's parameter dictionary
Match found! Replacing row...
Setting initial vbl value to NaN
Setting initial vbh value to NaN
Setting initial c value to NaN
Setting initial p value to NaN
Constant Vo

Setting initial vbl value to NaN
Setting initial vbh value to NaN
Setting initial c value to NaN
Setting initial p value to NaN
Constant Volatility Model: setting vbh to vbl, lambda to NaN
Setting parameter dictionary to batch object's parameter dictionary
Match found! Replacing row...
Setting initial vbl value to NaN
Setting initial vbh value to NaN
Setting initial c value to NaN
Setting initial p value to NaN
Constant Volatility Model: setting vbh to vbl, lambda to NaN
Setting parameter dictionary to batch object's parameter dictionary
Match found! Replacing row...
Setting initial vbl value to NaN
Setting initial vbh value to NaN
Setting initial c value to NaN
Setting initial p value to NaN
Constant Volatility Model: setting vbh to vbl, lambda to NaN
Setting parameter dictionary to batch object's parameter dictionary
Match found! Replacing row...
Setting initial vbl value to NaN
Setting initial vbh value to NaN
Setting initial c value to NaN
Setting initial p value to NaN
Constant Vo

Dict{Symbol,Any} with 5 entries:
  :m       => 1.0
  :opt_mbr => 208×36 DataFrame. Omitted printing of 30 columns…
  :model   => "cvm"
  :diag    => 1040×17 DataFrame. Omitted printing of 12 columns…
  :opt_fv  => 208×36 DataFrame. Omitted printing of 30 columns…

In [50]:
cvm_res[:opt_mbr]

208×36 DataFrame. Omitted printing of 30 columns
│ Row │ comb_num │ m       │ m_comb_num │ obj_fun │ gross_delta │ delta   │
│     │ Int64    │ Float64 │ Int64      │ String  │ Float64     │ Float64 │
├─────┼──────────┼─────────┼────────────┼─────────┼─────────────┼─────────┤
│ 1   │ 1        │ 1.0     │ 1          │ MBR     │ 0.02        │ 0.02    │
│ 2   │ 6        │ 1.0     │ 6          │ MBR     │ 0.02        │ 0.02    │
│ 3   │ 11       │ 1.0     │ 11         │ MBR     │ 0.02        │ 0.02    │
│ 4   │ 16       │ 1.0     │ 16         │ MBR     │ 0.02        │ 0.02    │
│ 5   │ 21       │ 1.0     │ 21         │ MBR     │ 0.02        │ 0.01995 │
│ 6   │ 26       │ 1.0     │ 26         │ MBR     │ 0.02        │ 0.01995 │
│ 7   │ 31       │ 1.0     │ 31         │ MBR     │ 0.02        │ 0.01995 │
│ 8   │ 36       │ 1.0     │ 36         │ MBR     │ 0.02        │ 0.01995 │
│ 9   │ 41       │ 1.0     │ 41         │ MBR     │ 0.02        │ 0.0199  │
│ 10  │ 46       │ 1.0     │ 46         │ MBR     │ 0.02        │ 0.0199  │
│ 11  │ 51       │ 1.0     │ 51         │ MBR     │ 0.02        │ 0.0199  │
│ 12  │ 56       │ 1.0     │ 56         │ MBR     │ 0.02        │ 0.0199  │
│ 13  │ 61       │ 1.0     │ 61         │ MBR     │ 0.02        │ 0.01985 │
│ 14  │ 66       │ 1.0     │ 66         │ MBR     │ 0.02        │ 0.01985 │
│ 15  │ 71       │ 1.0     │ 71         │ MBR     │ 0.02        │ 0.01985 │
│ 16  │ 76       │ 1.0     │ 76         │ MBR     │ 0.02        │ 0.01985 │
│ 17  │ 81       │ 1.0     │ 81         │ MBR     │ 0.02        │ 0.0198  │
│ 18  │ 86       │ 1.0     │ 86         │ MBR     │ 0.02        │ 0.0198  │
│ 19  │ 91       │ 1.0     │ 91         │ MBR     │ 0.02        │ 0.0198  │
│ 20  │ 96       │ 1.0     │ 96         │ MBR     │ 0.02        │ 0.0198  │
│ 21  │ 101      │ 1.0     │ 101        │ MBR     │ 0.02        │ 0.01975 │
│ 22  │ 106      │ 1.0     │ 106        │ MBR     │ 0.02        │ 0.01975 │
│ 23  │ 111      │ 1.0     │ 111        │ MBR     │ 0.02        │ 0.01975 │
│ 24  │ 116      │ 1.0     │ 116        │ MBR     │ 0.02        │ 0.01975 │
│ 25  │ 121      │ 1.0     │ 121        │ MBR     │ 0.02        │ 0.0195  │
│ 26  │ 126      │ 1.0     │ 126        │ MBR     │ 0.02        │ 0.0195  │
│ 27  │ 131      │ 1.0     │ 131        │ MBR     │ 0.02        │ 0.0195  │
│ 28  │ 136      │ 1.0     │ 136        │ MBR     │ 0.02        │ 0.0195  │
│ 29  │ 141      │ 1.0     │ 141        │ MBR     │ 0.02        │ 0.01925 │
│ 30  │ 146      │ 1.0     │ 146        │ MBR     │ 0.02        │ 0.01925 │
│ 31  │ 151      │ 1.0     │ 151        │ MBR     │ 0.02        │ 0.01925 │
│ 32  │ 156      │ 1.0     │ 156        │ MBR     │ 0.02        │ 0.01925 │
│ 33  │ 161      │ 1.0     │ 161        │ MBR     │ 0.02        │ 0.019   │
│ 34  │ 166      │ 1.0     │ 166        │ MBR     │ 0.02        │ 0.019   │
│ 35  │ 171      │ 1.0     │ 171        │ MBR     │ 0.02        │ 0.019   │
│ 36  │ 176      │ 1.0     │ 176        │ MBR     │ 0.02        │ 0.019   │
│ 37  │ 181      │ 1.0     │ 181        │ MBR     │ 0.02        │ 0.0185  │
│ 38  │ 186      │ 1.0     │ 186        │ MBR     │ 0.02        │ 0.0185  │
│ 39  │ 191      │ 1.0     │ 191        │ MBR     │ 0.02        │ 0.0185  │
│ 40  │ 196      │ 1.0     │ 196        │ MBR     │ 0.02        │ 0.0185  │
│ 41  │ 201      │ 1.0     │ 201        │ MBR     │ 0.02        │ 0.018   │
│ 42  │ 206      │ 1.0     │ 206        │ MBR     │ 0.02        │ 0.018   │
│ 43  │ 211      │ 1.0     │ 211        │ MBR     │ 0.02        │ 0.018   │
│ 44  │ 216      │ 1.0     │ 216        │ MBR     │ 0.02        │ 0.018   │
│ 45  │ 221      │ 1.0     │ 221        │ MBR     │ 0.02        │ 0.0175  │
│ 46  │ 226      │ 1.0     │ 226        │ MBR     │ 0.02        │ 0.0175  │
│ 47  │ 231      │ 1.0     │ 231        │ MBR     │ 0.02        │ 0.0175  │
│ 48  │ 236      │ 1.0     │ 236        │ MBR     │ 0.02        │ 0.0175  │
│ 49  │ 241      │ 1.0     │ 241        │ MBR     │ 0.02        │ 0.015   │

In [47]:
plot_script_path = string(main_path, "/Julia/Batch/")
plot_script_name = "diag_compilation.jl"
svm_res = include(string(plot_script_path, "/", plot_script_name))

  5.842672 seconds (7.33 M allocations: 386.666 MiB, 3.71% gc time)
Saving compiled results...
  6.016048 seconds (7.74 M allocations: 406.718 MiB, 3.80% gc time)
  4.209383 seconds (1.27 M allocations: 83.573 MiB, 0.95% gc time)
Saving compiled results...
  4.227312 seconds (1.29 M allocations: 84.622 MiB, 0.95% gc time)


Dict{Symbol,Any} with 5 entries:
  :m       => 1.0
  :opt_mbr => 150×38 DataFrame. Omitted printing of 32 columns…
  :model   => "svm"
  :diag    => 150×17 DataFrame. Omitted printing of 12 columns…
  :opt_fv  => 150×38 DataFrame. Omitted printing of 32 columns…

In [46]:
res[:opt_mbr]

150×38 DataFrame. Omitted printing of 32 columns
│ Row │ comb_num │ m       │ m_comb_num │ obj_fun │ gross_delta │ delta   │
│     │ Int64    │ Float64 │ Int64      │ String  │ Float64     │ Float64 │
├─────┼──────────┼─────────┼────────────┼─────────┼─────────────┼─────────┤
│ 1   │ 1        │ 1.0     │ 1          │ MBR     │ 0.02        │ 0.02    │
│ 2   │ 2        │ 1.0     │ 2          │ MBR     │ 0.02        │ 0.02    │
│ 3   │ 3        │ 1.0     │ 3          │ MBR     │ 0.02        │ 0.02    │
│ 4   │ 4        │ 1.0     │ 4          │ MBR     │ 0.02        │ 0.02    │
│ 5   │ 5        │ 1.0     │ 5          │ MBR     │ 0.02        │ 0.02    │
│ 6   │ 6        │ 1.0     │ 6          │ MBR     │ 0.02        │ 0.02    │
│ 7   │ 7        │ 1.0     │ 7          │ MBR     │ 0.02        │ 0.02    │
│ 8   │ 8        │ 1.0     │ 8          │ MBR     │ 0.02        │ 0.02    │
│ 9   │ 9        │ 1.0     │ 9          │ MBR     │ 0.02        │ 0.02    │
│ 10  │ 10       │ 1.0     │ 10         │ MBR     │ 0.02        │ 0.02    │
│ 11  │ 11       │ 1.0     │ 11         │ MBR     │ 0.02        │ 0.02    │
│ 12  │ 12       │ 1.0     │ 12         │ MBR     │ 0.02        │ 0.02    │
│ 13  │ 13       │ 1.0     │ 13         │ MBR     │ 0.02        │ 0.02    │
│ 14  │ 14       │ 1.0     │ 14         │ MBR     │ 0.02        │ 0.02    │
│ 15  │ 15       │ 1.0     │ 15         │ MBR     │ 0.02        │ 0.02    │
│ 16  │ 16       │ 1.0     │ 16         │ MBR     │ 0.02        │ 0.02    │
│ 17  │ 17       │ 1.0     │ 17         │ MBR     │ 0.02        │ 0.02    │
│ 18  │ 18       │ 1.0     │ 18         │ MBR     │ 0.02        │ 0.02    │
│ 19  │ 19       │ 1.0     │ 19         │ MBR     │ 0.02        │ 0.02    │
│ 20  │ 20       │ 1.0     │ 20         │ MBR     │ 0.02        │ 0.02    │
│ 21  │ 21       │ 1.0     │ 21         │ MBR     │ 0.02        │ 0.02    │
│ 22  │ 22       │ 1.0     │ 22         │ MBR     │ 0.02        │ 0.02    │
│ 23  │ 23       │ 1.0     │ 23         │ MBR     │ 0.02        │ 0.02    │
│ 24  │ 24       │ 1.0     │ 24         │ MBR     │ 0.02        │ 0.02    │
│ 25  │ 25       │ 1.0     │ 25         │ MBR     │ 0.02        │ 0.02    │
│ 26  │ 26       │ 1.0     │ 26         │ MBR     │ 0.02        │ 0.02    │
│ 27  │ 27       │ 1.0     │ 27         │ MBR     │ 0.02        │ 0.02    │
│ 28  │ 28       │ 1.0     │ 28         │ MBR     │ 0.02        │ 0.02    │
│ 29  │ 29       │ 1.0     │ 29         │ MBR     │ 0.02        │ 0.02    │
│ 30  │ 30       │ 1.0     │ 30         │ MBR     │ 0.02        │ 0.02    │
│ 31  │ 31       │ 1.0     │ 31         │ MBR     │ 0.02        │ 0.02    │
│ 32  │ 32       │ 1.0     │ 32         │ MBR     │ 0.02        │ 0.02    │
│ 33  │ 33       │ 1.0     │ 33         │ MBR     │ 0.02        │ 0.02    │
│ 34  │ 34       │ 1.0     │ 34         │ MBR     │ 0.02        │ 0.02    │
│ 35  │ 35       │ 1.0     │ 35         │ MBR     │ 0.02        │ 0.02    │
│ 36  │ 36       │ 1.0     │ 36         │ MBR     │ 0.02        │ 0.02    │
│ 37  │ 37       │ 1.0     │ 37         │ MBR     │ 0.02        │ 0.02    │
│ 38  │ 38       │ 1.0     │ 38         │ MBR     │ 0.02        │ 0.02    │
│ 39  │ 39       │ 1.0     │ 39         │ MBR     │ 0.02        │ 0.02    │
│ 40  │ 40       │ 1.0     │ 40         │ MBR     │ 0.02        │ 0.02    │
│ 41  │ 41       │ 1.0     │ 41         │ MBR     │ 0.02        │ 0.02    │
│ 42  │ 42       │ 1.0     │ 42         │ MBR     │ 0.02        │ 0.02    │
│ 43  │ 43       │ 1.0     │ 43         │ MBR     │ 0.02        │ 0.02    │
│ 44  │ 44       │ 1.0     │ 44         │ MBR     │ 0.02        │ 0.02    │
│ 45  │ 45       │ 1.0     │ 45         │ MBR     │ 0.02        │ 0.02    │
│ 46  │ 46       │ 1.0     │ 46         │ MBR     │ 0.02        │ 0.02    │
│ 47  │ 47       │ 1.0     │ 47         │ MBR     │ 0.02        │ 0.02    │
│ 48  │ 48       │ 1.0     │ 48         │ MBR     │ 0.02        │ 0.02    │
│ 49  │ 49       │ 1.0     │ 49         │ MBR     │ 0.02        │ 0.02    │

In [27]:
plot_script_path = string(main_path, "/Julia/Batch/compilation_scripts")
plot_script_name = "svm_compilation.jl"
optDFs = include(string(plot_script_path, "/", plot_script_name))

Loading SVM object...
Batch object file not found.
Batch Object is incompatible! Loading surfaces only instead.
Setting initial vbl value to NaN
Setting initial vbh value to NaN
Setting initial c value to NaN
Setting initial p value to NaN
Interpolating Bond Pricing Surfaces...


  0.216318 seconds (811.57 k allocations: 137.123 MiB, 13.96% gc time)
Batch object exists: true
Interpolating bond pricing surfaces...
  0.199884 seconds (811.42 k allocations: 137.112 MiB, 11.96% gc time)
 11.990374 seconds (36.70 M allocations: 1.626 GiB, 10.79% gc time)
P Filter Conditions Satisfied! Exiting...
c: 0.5 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 1.0 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 1.5 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 2.0 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 2.5 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 3.0 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 3.5 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 4.0 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 4.5 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 5.0 -> P Filter success!
P Filter Conditions Satis

Computing equity values... 
V0: 100.0; equity: 58.55615372999389
Equity Core Function Computation Time: 0.1539599895477295
Total Equity FD Core Function Computation Time: 0.24034690856933594
Total computation time: 0.26932287216186523
Setting parameter dictionary to batch object's parameter dictionary
Loading SVM object...
Batch object file not found.
Batch Object is incompatible! Loading surfaces only instead.
Setting initial vbl value to NaN
Setting initial vbh value to NaN
Setting initial c value to NaN
Setting initial p value to NaN
Interpolating Bond Pricing Surfaces...
  0.197462 seconds (811.43 k allocations: 137.115 MiB, 8.70% gc time)
Batch object exists: true
Interpolating bond pricing surfaces...
  0.183414 seconds (811.43 k allocations: 137.112 MiB, 6.65% gc time)
  0.595260 seconds (159.19 k allocations: 72.538 MiB, 1.88% gc time)
P Filter Conditions Satisfied! Exiting...
c: 0.5 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 1.0 -> P Filter success!
P Fi

Computing equity values... 
V0: 100.0; equity: 59.52950373601709
Equity Core Function Computation Time: 0.15010905265808105
Total Equity FD Core Function Computation Time: 0.23276090621948242
Total computation time: 0.2633931636810303
Setting parameter dictionary to batch object's parameter dictionary
Loading SVM object...
Batch object file not found.
Batch Object is incompatible! Loading surfaces only instead.
Setting initial vbl value to NaN
Setting initial vbh value to NaN
Setting initial c value to NaN
Setting initial p value to NaN
Interpolating Bond Pricing Surfaces...
  0.198315 seconds (811.43 k allocations: 137.115 MiB, 9.12% gc time)
Batch object exists: true
Interpolating bond pricing surfaces...
  0.184380 seconds (811.42 k allocations: 137.112 MiB, 8.44% gc time)
  0.563956 seconds (165.40 k allocations: 73.508 MiB, 2.22% gc time)
P Filter Conditions Satisfied! Exiting...
c: 0.5 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 1.0 -> P Filter success!
P Fi

Computing equity values... 
V0: 100.0; equity: 60.04579791744789
Equity Core Function Computation Time: 0.15281105041503906
Total Equity FD Core Function Computation Time: 0.2387831211090088
Total computation time: 0.26639819145202637
Setting parameter dictionary to batch object's parameter dictionary
Loading SVM object...
Batch object file not found.
Batch Object is incompatible! Loading surfaces only instead.
Setting initial vbl value to NaN
Setting initial vbh value to NaN
Setting initial c value to NaN
Setting initial p value to NaN
Interpolating Bond Pricing Surfaces...
  0.198734 seconds (811.43 k allocations: 137.115 MiB, 9.36% gc time)
Batch object exists: true
Interpolating bond pricing surfaces...
  0.182931 seconds (811.43 k allocations: 137.113 MiB, 7.55% gc time)
  0.590375 seconds (168.27 k allocations: 76.261 MiB, 1.94% gc time)
P Filter Conditions Satisfied! Exiting...
c: 0.5 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 1.0 -> P Filter success!
P Fi

...

P Filter Conditions Satisfied! Exiting...
c: 5.5 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 6.0 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 6.5 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 7.0 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 7.5 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 8.0 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 8.5 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 9.0 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 9.5 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 10.0 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 10.5 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 11.0 -> P Filter success!
  0.248175 seconds (11.05 k allocations: 86.057 MiB, 4.75% gc time)
Computing Equity Vmax
Vmax: 125.0
phi0: -40.15536178477692
phi1: 0.9999999999999998
pv_rf

P Filter Conditions Satisfied! Exiting...
c: 4.0 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 4.5 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 5.0 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 5.5 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 6.0 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 6.5 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 7.0 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 7.5 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 8.0 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 8.5 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 9.0 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 9.5 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 10.0 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 10.5 -> P Filter success!
P Filter Condition

Excessive output truncated after 524291 bytes.

  0.357033 seconds (155.90 k allocations: 76.473 MiB, 3.28% gc time)
P Filter Conditions Satisfied! Exiting...
c: 0.5 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 1.0 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 1.5 -> P Filter success!


2-element Array{Any,1}:
 150×38 DataFrame. Omitted printing of 32 columns
│ Row │ comb_num │ m       │ m_comb_num │ obj_fun    │ gross_delta │ delta   │
│     │ Int64    │ Float64 │ Int64      │ String     │ Float64     │ Float64 │
├─────┼──────────┼─────────┼────────────┼────────────┼─────────────┼─────────┤
│ 1   │ 1        │ 1.0     │ 1          │ firm_value │ 0.02        │ 0.02    │
│ 2   │ 2        │ 1.0     │ 2          │ firm_value │ 0.02        │ 0.02    │
│ 3   │ 3        │ 1.0     │ 3          │ firm_value │ 0.02        │ 0.02    │
│ 4   │ 4        │ 1.0     │ 4          │ firm_value │ 0.02        │ 0.02    │
│ 5   │ 5        │ 1.0     │ 5          │ firm_value │ 0.02        │ 0.02    │
│ 6   │ 6        │ 1.0     │ 6          │ firm_value │ 0.02        │ 0.02    │
│ 7   │ 7        │ 1.0     │ 7          │ firm_value │ 0.02        │ 0.02    │
│ 8   │ 8        │ 1.0     │ 8          │ firm_value │ 0.02        │ 0.02    │
│ 9   │ 9        │ 1.0     │ 9          │ firm_value │ 0.

In [176]:
modls = ["Batch", "ModelObj", "AnalyticFunctions", 
         "BondPrInterp", "EqFinDiff"]
for modl in modls
    include(string(joinpath(module_path, modl), "/", modl, ".jl"))
end

In [185]:
Batch.load_svm_opt_results_df(bt; firm_obj_fun=:MBR, m=1.)

Setting parameter dictionary using (m, m_comb_num) ID pair...
Loading optimal results dataframe...


MethodError: MethodError: Cannot `convert` an object of type Missing to an object of type Float64
Closest candidates are:
  convert(::Type{T<:AbstractFloat}, !Matched::Ratios.SimpleRatio{S}) where {T<:AbstractFloat, S} at /home/artur/.julia/packages/Ratios/iJ67w/src/Ratios.jl:16
  convert(::Type{T<:Number}, !Matched::T<:Number) where T<:Number at number.jl:6
  convert(::Type{T<:Number}, !Matched::Number) where T<:Number at number.jl:7
  ...

In [17]:
modls = ["Batch", "ModelObj", "AnalyticFunctions", 
         "BondPrInterp", "EqFinDiff"]
for modl in modls
    include(string(joinpath(module_path, modl), "/", modl, ".jl"))
end

Batch.load_svm_opt_results(bt; comb_num=142, save_optdf=false)

Setting parameter dictionary using unique combination ID...


1×38 DataFrame. Omitted printing of 32 columns
│ Row │ comb_num │ m       │ m_comb_num │ obj_fun    │ gross_delta │ delta   │
│     │ Int64    │ Float64 │ Int64      │ String     │ Float64     │ Float64 │
├─────┼──────────┼─────────┼────────────┼────────────┼─────────────┼─────────┤
│ 1   │ 142      │ 1.0     │ 142        │ firm_value │ 0.02        │ 0.02    │

In [14]:
modls = ["Batch", "ModelObj", "AnalyticFunctions", 
         "BondPrInterp", "EqFinDiff"]
for modl in modls
    include(string(joinpath(module_path, modl), "/", modl, ".jl"))
end

optDF_fv = @time Batch.compile_svm_opt_results(bt; m=1., firm_obj_fun=:firm_value, 
    replace_optdf=true)

Batch object exists: true
Loading SVM object...
Unable to load batch object file.
Batch Object is incompatible! Loading surfaces only instead.
Setting initial vbl value to NaN
Setting initial vbh value to NaN
Setting initial c value to NaN
Setting initial p value to NaN


Interpolating Bond Pricing Surfaces...
  0.257812 seconds (811.42 k allocations: 137.112 MiB, 14.49% gc time)
Interpolating bond pricing surfaces...
  0.243685 seconds (811.43 k allocations: 137.112 MiB, 14.19% gc time)
  1.973398 seconds (3.58 M allocations: 237.368 MiB, 6.85% gc time)
P Filter Conditions Satisfied! Exiting...
c: 0.5 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 1.0 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 1.5 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 2.0 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 2.5 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 3.0 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 3.5 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 4.0 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 4.5 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 5.0 -> P Filter success!
P Filter Con

Computing equity values... 
V0: 100.0; equity: 58.543890793764675
Equity Core Function Computation Time: 0.15604496002197266
Total Equity FD Core Function Computation Time: 0.2350599765777588
Total computation time: 0.26885509490966797
Setting parameter dictionary to batch object's parameter dictionary
Batch object exists: true
Loading SVM object...
Unable to load batch object file.
Batch Object is incompatible! Loading surfaces only instead.
Setting initial vbl value to NaN
Setting initial vbh value to NaN
Setting initial c value to NaN
Setting initial p value to NaN
Interpolating Bond Pricing Surfaces...
  0.245623 seconds (811.43 k allocations: 137.112 MiB, 10.82% gc time)
Interpolating bond pricing surfaces...
  0.238552 seconds (811.43 k allocations: 137.112 MiB, 13.19% gc time)
  0.630791 seconds (149.30 k allocations: 70.761 MiB, 2.61% gc time)
P Filter Conditions Satisfied! Exiting...
c: 0.5 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 1.0 -> P Filter succe

Computing equity values... 
V0: 100.0; equity: 59.54045951641345
Equity Core Function Computation Time: 0.1794571876525879
Total Equity FD Core Function Computation Time: 0.2584989070892334
Total computation time: 0.2926039695739746
Setting parameter dictionary to batch object's parameter dictionary
Batch object exists: true
Loading SVM object...
Unable to load batch object file.
Batch Object is incompatible! Loading surfaces only instead.
Setting initial vbl value to NaN
Setting initial vbh value to NaN
Setting initial c value to NaN
Setting initial p value to NaN
Interpolating Bond Pricing Surfaces...
  0.250329 seconds (811.43 k allocations: 137.112 MiB, 11.21% gc time)
Interpolating bond pricing surfaces...
  0.231197 seconds (811.43 k allocations: 137.113 MiB, 11.54% gc time)
  0.643385 seconds (147.62 k allocations: 70.487 MiB, 2.63% gc time)
P Filter Conditions Satisfied! Exiting...
c: 0.5 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 1.0 -> P Filter success!

debt_abs_per_diff: 1.2706720412283137e-8
eq_abs_per_diff: 0.0008215182200820811
Equity Vmax: 259.86602242642107
 
eq_max: 222.66551899044947
eq_vbl: 0.0
Computing Constant Volatility Equity Values
Finished computing Constant Volatility Equity Values
Time to compute Constant Volatility Equity Values: 0.010014057159423828
 
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 60.04172241059048
Equity Core Function Computation Time: 0.18310093879699707
Total Equity FD Core Function Computation Time: 0.28821301460266113
Total computation time: 0.322979211807251
Setting parameter dictionary to batch object's parameter dictionary
Batch object exists: true
Loading SVM object...
Unable to load batch object file.
Batch Object is incompatible! Loading surfaces only instead.
Setting initial vbl value to NaN
Setting initial vbh value to NaN
Setting initial c value to NaN
Setting initial p value to NaN
Interpolating Bond Pricing Surfaces...
  0.248445 seconds (811.44 k allo

...

Computing equity values... 
V0: 100.0; equity: 72.41443078687429
Equity Core Function Computation Time: 0.1748650074005127
Total Equity FD Core Function Computation Time: 0.25758790969848633
Total computation time: 0.32311081886291504
Setting parameter dictionary to batch object's parameter dictionary
Batch object exists: true
Loading SVM object...
Unable to load batch object file.
Batch Object is incompatible! Loading surfaces only instead.
Setting initial vbl value to NaN
Setting initial vbh value to NaN
Setting initial c value to NaN
Setting initial p value to NaN
Interpolating Bond Pricing Surfaces...
  0.244601 seconds (811.44 k allocations: 137.115 MiB, 10.81% gc time)
Interpolating bond pricing surfaces...
  0.231996 seconds (811.43 k allocations: 137.112 MiB, 11.06% gc time)
  0.861239 seconds (147.19 k allocations: 72.417 MiB, 2.03% gc time)
P Filter Conditions Satisfied! Exiting...
c: 0.5 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 1.0 -> P Filter succes

Computing equity values... 
V0: 100.0; equity: 78.17924587434882
Equity Core Function Computation Time: 0.17210888862609863
Total Equity FD Core Function Computation Time: 0.2526359558105469
Total computation time: 0.3113560676574707
Setting parameter dictionary to batch object's parameter dictionary
Batch object exists: true
Loading SVM object...
Unable to load batch object file.
Batch Object is incompatible! Loading surfaces only instead.
Setting initial vbl value to NaN
Setting initial vbh value to NaN
Setting initial c value to NaN
Setting initial p value to NaN
Interpolating Bond Pricing Surfaces...
  0.244165 seconds (811.43 k allocations: 137.115 MiB, 10.61% gc time)
Interpolating bond pricing surfaces...
  0.230587 seconds (811.43 k allocations: 137.112 MiB, 10.70% gc time)
  0.827425 seconds (150.04 k allocations: 72.925 MiB, 1.95% gc time)
P Filter Conditions Satisfied! Exiting...
c: 0.5 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 1.0 -> P Filter success

debt_abs_per_diff: 3.3075364920205613e-7
eq_abs_per_diff: 0.0009021162929443949
Equity Vmax: 514.5169494226984
 
eq_max: 496.7646421666393
eq_vbl: 0.0
Computing Constant Volatility Equity Values
Finished computing Constant Volatility Equity Values
Time to compute Constant Volatility Equity Values: 0.009948015213012695
 
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 79.92921455602863
Equity Core Function Computation Time: 0.17224693298339844
Total Equity FD Core Function Computation Time: 0.2563140392303467
Total computation time: 0.3098921775817871
Setting parameter dictionary to batch object's parameter dictionary
Batch object exists: true
Loading SVM object...
Unable to load batch object file.
Batch Object is incompatible! Loading surfaces only instead.
Setting initial vbl value to NaN
Setting initial vbh value to NaN
Setting initial c value to NaN
Setting initial p value to NaN
Interpolating Bond Pricing Surfaces...
  0.243999 seconds (811.44 k alloca

c: 11.0 -> P Filter failed...
  1.654064 seconds (15.82 k allocations: 560.782 MiB, 6.48% gc time)
Computing Equity Vmax
Vmax: 125.0
phi0: -17.497967559427696
phi1: 0.9999999999999998
pv_rfdebt: 23.095489320181926
debt_abs_per_diff: 3.2341207115475557e-7
eq_abs_per_diff: 0.000938420625586009
Equity Vmax: 514.5169494226984
 
eq_max: 497.0189812538088
eq_vbl: 0.0
Computing Constant Volatility Equity Values
Finished computing Constant Volatility Equity Values
Time to compute Constant Volatility Equity Values: 0.008355855941772461
 
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 79.92551434692297
Equity Core Function Computation Time: 0.15621304512023926
Total Equity FD Core Function Computation Time: 0.23056983947753906
Total computation time: 0.2748849391937256
Setting parameter dictionary to batch object's parameter dictionary
Batch object exists: true
Loading SVM object...
Unable to load batch object file.
Batch Object is incompatible! Loading surfaces on

150×38 DataFrame. Omitted printing of 32 columns
│ Row │ comb_num │ m       │ m_comb_num │ obj_fun    │ gross_delta │ delta   │
│     │ Int64    │ Float64 │ Int64      │ String     │ Float64     │ Float64 │
├─────┼──────────┼─────────┼────────────┼────────────┼─────────────┼─────────┤
│ 1   │ 1        │ 1.0     │ 1          │ firm_value │ 0.02        │ 0.02    │
│ 2   │ 2        │ 1.0     │ 2          │ firm_value │ 0.02        │ 0.02    │
│ 3   │ 3        │ 1.0     │ 3          │ firm_value │ 0.02        │ 0.02    │
│ 4   │ 4        │ 1.0     │ 4          │ firm_value │ 0.02        │ 0.02    │
│ 5   │ 5        │ 1.0     │ 5          │ firm_value │ 0.02        │ 0.02    │
│ 6   │ 6        │ 1.0     │ 6          │ firm_value │ 0.02        │ 0.02    │
│ 7   │ 7        │ 1.0     │ 7          │ firm_value │ 0.02        │ 0.02    │
│ 8   │ 8        │ 1.0     │ 8          │ firm_value │ 0.02        │ 0.02    │
│ 9   │ 9        │ 1.0     │ 9          │ firm_value │ 0.02        │ 0.02    │
│ 10  │ 10       │ 1.0     │ 10         │ firm_value │ 0.02        │ 0.02    │
⋮
│ 140 │ 140      │ 1.0     │ 140        │ firm_value │ 0.02        │ 0.02    │
│ 141 │ 141      │ 1.0     │ 141        │ firm_value │ 0.02        │ 0.02    │
│ 142 │ 142      │ 1.0     │ 142        │ firm_value │ 0.02        │ 0.02    │
│ 143 │ 143      │ 1.0     │ 143        │ firm_value │ 0.02        │ 0.02    │
│ 144 │ 144      │ 1.0     │ 144        │ firm_value │ 0.02        │ 0.02    │
│ 145 │ 145      │ 1.0     │ 145        │ firm_value │ 0.02        │ 0.02    │
│ 146 │ 146      │ 1.0     │ 146        │ firm_value │ 0.02        │ 0.02    │
│ 147 │ 147      │ 1.0     │ 147        │ firm_value │ 0.02        │ 0.02    │
│ 148 │ 148      │ 1.0     │ 148        │ firm_value │ 0.02        │ 0.02    │
│ 149 │ 149      │ 1.0     │ 149        │ firm_value │ 0.02        │ 0.02    │
│ 150 │ 150      │ 1.0     │ 150        │ firm_value │ 0.02        │ 0.02    │

In [18]:
optDF_fv2 = @time Batch.compile_svm_opt_results(bt; m=1., firm_obj_fun=:firm_value, 
                                                recompute_comb_opt_res=false)

  1.504723 seconds (3.35 M allocations: 180.182 MiB, 8.08% gc time)
Saving compiled results...
  1.882493 seconds (4.33 M allocations: 228.954 MiB, 7.19% gc time)


150×38 DataFrame. Omitted printing of 32 columns
│ Row │ comb_num │ m       │ m_comb_num │ obj_fun    │ gross_delta │ delta   │
│     │ Int64    │ Float64 │ Int64      │ String     │ Float64     │ Float64 │
├─────┼──────────┼─────────┼────────────┼────────────┼─────────────┼─────────┤
│ 1   │ 1        │ 1.0     │ 1          │ firm_value │ 0.02        │ 0.02    │
│ 2   │ 2        │ 1.0     │ 2          │ firm_value │ 0.02        │ 0.02    │
│ 3   │ 3        │ 1.0     │ 3          │ firm_value │ 0.02        │ 0.02    │
│ 4   │ 4        │ 1.0     │ 4          │ firm_value │ 0.02        │ 0.02    │
│ 5   │ 5        │ 1.0     │ 5          │ firm_value │ 0.02        │ 0.02    │
│ 6   │ 6        │ 1.0     │ 6          │ firm_value │ 0.02        │ 0.02    │
│ 7   │ 7        │ 1.0     │ 7          │ firm_value │ 0.02        │ 0.02    │
│ 8   │ 8        │ 1.0     │ 8          │ firm_value │ 0.02        │ 0.02    │
│ 9   │ 9        │ 1.0     │ 9          │ firm_value │ 0.02        │ 0.02    │
│ 10  │ 10       │ 1.0     │ 10         │ firm_value │ 0.02        │ 0.02    │
⋮
│ 140 │ 140      │ 1.0     │ 140        │ firm_value │ 0.02        │ 0.02    │
│ 141 │ 141      │ 1.0     │ 141        │ firm_value │ 0.02        │ 0.02    │
│ 142 │ 142      │ 1.0     │ 142        │ firm_value │ 0.02        │ 0.02    │
│ 143 │ 143      │ 1.0     │ 143        │ firm_value │ 0.02        │ 0.02    │
│ 144 │ 144      │ 1.0     │ 144        │ firm_value │ 0.02        │ 0.02    │
│ 145 │ 145      │ 1.0     │ 145        │ firm_value │ 0.02        │ 0.02    │
│ 146 │ 146      │ 1.0     │ 146        │ firm_value │ 0.02        │ 0.02    │
│ 147 │ 147      │ 1.0     │ 147        │ firm_value │ 0.02        │ 0.02    │
│ 148 │ 148      │ 1.0     │ 148        │ firm_value │ 0.02        │ 0.02    │
│ 149 │ 149      │ 1.0     │ 149        │ firm_value │ 0.02        │ 0.02    │
│ 150 │ 150      │ 1.0     │ 150        │ firm_value │ 0.02        │ 0.02    │

In [19]:
optDF_mbr  = @time Batch.compile_svm_opt_results(bt; m=1., firm_obj_fun=:MBR)

Batch object exists: true
Loading SVM object...
Unable to load batch object file.
Batch Object is incompatible! Loading surfaces only instead.
Setting initial vbl value to NaN
Setting initial vbh value to NaN
Setting initial c value to NaN
Setting initial p value to NaN
Interpolating Bond Pricing Surfaces...
  0.218850 seconds (811.43 k allocations: 137.113 MiB, 16.15% gc time)
Interpolating bond pricing surfaces...
  0.206665 seconds (811.43 k allocations: 137.113 MiB, 16.06% gc time)
  1.894028 seconds (3.52 M allocations: 234.614 MiB, 7.28% gc time)
P Filter Conditions Satisfied! Exiting...
c: 0.5 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 1.0 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 1.5 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 2.0 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 2.5 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 3.0 -> P Filter success!
P Filter Conditions S

Computing equity values... 
V0: 100.0; equity: 49.06900758385221
Equity Core Function Computation Time: 0.16717791557312012
Total Equity FD Core Function Computation Time: 0.2475118637084961
Total computation time: 0.2808380126953125
Setting parameter dictionary to batch object's parameter dictionary
No match found. Appending row...
Batch object exists: true
Loading SVM object...
Unable to load batch object file.
Batch Object is incompatible! Loading surfaces only instead.
Setting initial vbl value to NaN
Setting initial vbh value to NaN
Setting initial c value to NaN
Setting initial p value to NaN
Interpolating Bond Pricing Surfaces...
  0.213915 seconds (811.47 k allocations: 137.116 MiB, 13.63% gc time)
Interpolating bond pricing surfaces...
  0.201371 seconds (811.43 k allocations: 137.112 MiB, 14.16% gc time)
  0.488714 seconds (149.09 k allocations: 70.754 MiB, 3.71% gc time)
P Filter Conditions Satisfied! Exiting...
c: 0.5 -> P Filter success!
P Filter Conditions Satisfied! Exit

debt_abs_per_diff: 7.96796320353552e-9
eq_abs_per_diff: 0.0009276902710600776
Equity Vmax: 300.8274042113857
 
eq_max: 258.05495935676856
eq_vbl: 0.0
Computing Constant Volatility Equity Values
Finished computing Constant Volatility Equity Values
Time to compute Constant Volatility Equity Values: 0.008279085159301758
 
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 51.33911915652775
Equity Core Function Computation Time: 0.16018986701965332
Total Equity FD Core Function Computation Time: 0.2501339912414551
Total computation time: 0.2823190689086914
Setting parameter dictionary to batch object's parameter dictionary
No match found. Appending row...
Batch object exists: true
Loading SVM object...
Unable to load batch object file.
Batch Object is incompatible! Loading surfaces only instead.
Setting initial vbl value to NaN
Setting initial vbh value to NaN
Setting initial c value to NaN
Setting initial p value to NaN
Interpolating Bond Pricing Surfaces...
  0

P Filter Conditions Satisfied! Exiting...
c: 9.0 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 9.5 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 10.0 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 10.5 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 11.0 -> P Filter success!
  0.300653 seconds (11.08 k allocations: 97.696 MiB, 8.54% gc time)
Computing Equity Vmax
Vmax: 125.0
phi0: -42.967125123835004
phi1: 0.9999999999999998
pv_rfdebt: 56.03631521373343
debt_abs_per_diff: 3.997500125047575e-9
eq_abs_per_diff: 0.0008119235110648099
Equity Vmax: 300.8274042113857
 
eq_max: 257.85593605424634
eq_vbl: 0.0
Computing Constant Volatility Equity Values
Finished computing Constant Volatility Equity Values
Time to compute Constant Volatility Equity Values: 0.008260965347290039
 
Shape of Gamma matrix: (1498,)
Computing equity values... 
V0: 100.0; equity: 51.89851052897305
Equity Core Function Computation Time: 0.161083

P Filter Conditions Satisfied! Exiting...
c: 7.5 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 8.0 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 8.5 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 9.0 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 9.5 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 10.0 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 10.5 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 11.0 -> P Filter success!
  0.644608 seconds (12.08 k allocations: 210.178 MiB, 9.21% gc time)
Computing Equity Vmax
Vmax: 125.0
phi0: -41.6886286174793
phi1: 0.9999999999999998
pv_rfdebt: 55.36175775601077
debt_abs_per_diff: 2.8715132569536905e-9
eq_abs_per_diff: 0.000952220569090533
Equity Vmax: 286.50228972512923
 
eq_max: 244.8084889469594
eq_vbl: 0.0
Computing Constant Volatility Equity Values
Finished computing Constant Volatility Equity Values
Time to 

...

P Filter Conditions Satisfied! Exiting...
c: 7.0 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 7.5 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 8.0 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 8.5 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 9.0 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 9.5 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 10.0 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 10.5 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 11.0 -> P Filter success!
  0.448127 seconds (11.44 k allocations: 132.335 MiB, 6.14% gc time)
Computing Equity Vmax
Vmax: 125.0
phi0: -24.172049186765143
phi1: 0.9999999999999998
pv_rfdebt: 31.846897143216882
debt_abs_per_diff: 2.4782777335568336e-7
eq_abs_per_diff: 0.0009975766969407829
Equity Vmax: 689.5019209490317
 
eq_max: 665.3298707709612
eq_vbl: 0.0
Computing Constant Volatility Eq

P Filter Conditions Satisfied! Exiting...
c: 4.0 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 4.5 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 5.0 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 5.5 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 6.0 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 6.5 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 7.0 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 7.5 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 8.0 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 8.5 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 9.0 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 9.5 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 10.0 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 10.5 -> P Filter success!
P Filter Condition

  0.229408 seconds (811.43 k allocations: 137.112 MiB, 11.08% gc time)
  0.513481 seconds (151.88 k allocations: 71.042 MiB, 3.13% gc time)
P Filter Conditions Satisfied! Exiting...
c: 0.5 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 1.0 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 1.5 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 2.0 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 2.5 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 3.0 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 3.5 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 4.0 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 4.5 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 5.0 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 5.5 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 6.0 -> P Filter success!
P Filter Conditions 

  0.208470 seconds (811.47 k allocations: 137.116 MiB, 12.09% gc time)
Interpolating bond pricing surfaces...
  0.197498 seconds (811.44 k allocations: 137.113 MiB, 12.41% gc time)
  0.494423 seconds (150.76 k allocations: 70.797 MiB, 3.23% gc time)
P Filter Conditions Satisfied! Exiting...
c: 0.5 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 1.0 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 1.5 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 2.0 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 2.5 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 3.0 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 3.5 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 4.0 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 4.5 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 5.0 -> P Filter success!
P Filter Conditions Satisfied! Exiting...
c: 5.5 -

150×38 DataFrame. Omitted printing of 32 columns
│ Row │ comb_num │ m       │ m_comb_num │ obj_fun │ gross_delta │ delta   │
│     │ Int64    │ Float64 │ Int64      │ String  │ Float64     │ Float64 │
├─────┼──────────┼─────────┼────────────┼─────────┼─────────────┼─────────┤
│ 1   │ 1        │ 1.0     │ 1          │ MBR     │ 0.02        │ 0.02    │
│ 2   │ 2        │ 1.0     │ 2          │ MBR     │ 0.02        │ 0.02    │
│ 3   │ 3        │ 1.0     │ 3          │ MBR     │ 0.02        │ 0.02    │
│ 4   │ 4        │ 1.0     │ 4          │ MBR     │ 0.02        │ 0.02    │
│ 5   │ 5        │ 1.0     │ 5          │ MBR     │ 0.02        │ 0.02    │
│ 6   │ 6        │ 1.0     │ 6          │ MBR     │ 0.02        │ 0.02    │
│ 7   │ 7        │ 1.0     │ 7          │ MBR     │ 0.02        │ 0.02    │
│ 8   │ 8        │ 1.0     │ 8          │ MBR     │ 0.02        │ 0.02    │
│ 9   │ 9        │ 1.0     │ 9          │ MBR     │ 0.02        │ 0.02    │
│ 10  │ 10       │ 1.0     │ 10         │ MBR     │ 0.02        │ 0.02    │
⋮
│ 140 │ 140      │ 1.0     │ 140        │ MBR     │ 0.02        │ 0.02    │
│ 141 │ 141      │ 1.0     │ 141        │ MBR     │ 0.02        │ 0.02    │
│ 142 │ 142      │ 1.0     │ 142        │ MBR     │ 0.02        │ 0.02    │
│ 143 │ 143      │ 1.0     │ 143        │ MBR     │ 0.02        │ 0.02    │
│ 144 │ 144      │ 1.0     │ 144        │ MBR     │ 0.02        │ 0.02    │
│ 145 │ 145      │ 1.0     │ 145        │ MBR     │ 0.02        │ 0.02    │
│ 146 │ 146      │ 1.0     │ 146        │ MBR     │ 0.02        │ 0.02    │
│ 147 │ 147      │ 1.0     │ 147        │ MBR     │ 0.02        │ 0.02    │
│ 148 │ 148      │ 1.0     │ 148        │ MBR     │ 0.02        │ 0.02    │
│ 149 │ 149      │ 1.0     │ 149        │ MBR     │ 0.02        │ 0.02    │
│ 150 │ 150      │ 1.0     │ 150        │ MBR     │ 0.02        │ 0.02    │

In [21]:
Batch.load_svm_opt_results_df(bt;
                                 firm_obj_fun=:firm_value,
                                 m=1.)

Setting parameter dictionary using (m, m_comb_num) ID pair...
Loading optimal results dataframe...


150×38 DataFrame. Omitted printing of 32 columns
│ Row │ comb_num │ m       │ m_comb_num │ obj_fun    │ gross_delta │ delta   │
│     │ Int64    │ Float64 │ Int64      │ String     │ Float64     │ Float64 │
├─────┼──────────┼─────────┼────────────┼────────────┼─────────────┼─────────┤
│ 1   │ 1        │ 1.0     │ 1          │ firm_value │ 0.02        │ 0.02    │
│ 2   │ 2        │ 1.0     │ 2          │ firm_value │ 0.02        │ 0.02    │
│ 3   │ 3        │ 1.0     │ 3          │ firm_value │ 0.02        │ 0.02    │
│ 4   │ 4        │ 1.0     │ 4          │ firm_value │ 0.02        │ 0.02    │
│ 5   │ 5        │ 1.0     │ 5          │ firm_value │ 0.02        │ 0.02    │
│ 6   │ 6        │ 1.0     │ 6          │ firm_value │ 0.02        │ 0.02    │
│ 7   │ 7        │ 1.0     │ 7          │ firm_value │ 0.02        │ 0.02    │
│ 8   │ 8        │ 1.0     │ 8          │ firm_value │ 0.02        │ 0.02    │
│ 9   │ 9        │ 1.0     │ 9          │ firm_value │ 0.02        │ 0.02    │
│ 10  │ 10       │ 1.0     │ 10         │ firm_value │ 0.02        │ 0.02    │
⋮
│ 140 │ 140      │ 1.0     │ 140        │ firm_value │ 0.02        │ 0.02    │
│ 141 │ 141      │ 1.0     │ 141        │ firm_value │ 0.02        │ 0.02    │
│ 142 │ 142      │ 1.0     │ 142        │ firm_value │ 0.02        │ 0.02    │
│ 143 │ 143      │ 1.0     │ 143        │ firm_value │ 0.02        │ 0.02    │
│ 144 │ 144      │ 1.0     │ 144        │ firm_value │ 0.02        │ 0.02    │
│ 145 │ 145      │ 1.0     │ 145        │ firm_value │ 0.02        │ 0.02    │
│ 146 │ 146      │ 1.0     │ 146        │ firm_value │ 0.02        │ 0.02    │
│ 147 │ 147      │ 1.0     │ 147        │ firm_value │ 0.02        │ 0.02    │
│ 148 │ 148      │ 1.0     │ 148        │ firm_value │ 0.02        │ 0.02    │
│ 149 │ 149      │ 1.0     │ 149        │ firm_value │ 0.02        │ 0.02    │
│ 150 │ 150      │ 1.0     │ 150        │ firm_value │ 0.02        │ 0.02    │

In [20]:
Batch.load_svm_opt_results_df(bt;
                                 firm_obj_fun=:MBR,
                                 m=1.)


Setting parameter dictionary using (m, m_comb_num) ID pair...
Loading optimal results dataframe...


150×38 DataFrame. Omitted printing of 32 columns
│ Row │ comb_num │ m       │ m_comb_num │ obj_fun │ gross_delta │ delta   │
│     │ Int64    │ Float64 │ Int64      │ String  │ Float64     │ Float64 │
├─────┼──────────┼─────────┼────────────┼─────────┼─────────────┼─────────┤
│ 1   │ 1        │ 1.0     │ 1          │ MBR     │ 0.02        │ 0.02    │
│ 2   │ 2        │ 1.0     │ 2          │ MBR     │ 0.02        │ 0.02    │
│ 3   │ 3        │ 1.0     │ 3          │ MBR     │ 0.02        │ 0.02    │
│ 4   │ 4        │ 1.0     │ 4          │ MBR     │ 0.02        │ 0.02    │
│ 5   │ 5        │ 1.0     │ 5          │ MBR     │ 0.02        │ 0.02    │
│ 6   │ 6        │ 1.0     │ 6          │ MBR     │ 0.02        │ 0.02    │
│ 7   │ 7        │ 1.0     │ 7          │ MBR     │ 0.02        │ 0.02    │
│ 8   │ 8        │ 1.0     │ 8          │ MBR     │ 0.02        │ 0.02    │
│ 9   │ 9        │ 1.0     │ 9          │ MBR     │ 0.02        │ 0.02    │
│ 10  │ 10       │ 1.0     │ 10         │ MBR     │ 0.02        │ 0.02    │
⋮
│ 140 │ 140      │ 1.0     │ 140        │ MBR     │ 0.02        │ 0.02    │
│ 141 │ 141      │ 1.0     │ 141        │ MBR     │ 0.02        │ 0.02    │
│ 142 │ 142      │ 1.0     │ 142        │ MBR     │ 0.02        │ 0.02    │
│ 143 │ 143      │ 1.0     │ 143        │ MBR     │ 0.02        │ 0.02    │
│ 144 │ 144      │ 1.0     │ 144        │ MBR     │ 0.02        │ 0.02    │
│ 145 │ 145      │ 1.0     │ 145        │ MBR     │ 0.02        │ 0.02    │
│ 146 │ 146      │ 1.0     │ 146        │ MBR     │ 0.02        │ 0.02    │
│ 147 │ 147      │ 1.0     │ 147        │ MBR     │ 0.02        │ 0.02    │
│ 148 │ 148      │ 1.0     │ 148        │ MBR     │ 0.02        │ 0.02    │
│ 149 │ 149      │ 1.0     │ 149        │ MBR     │ 0.02        │ 0.02    │
│ 150 │ 150      │ 1.0     │ 150        │ MBR     │ 0.02        │ 0.02    │

In [ ]:
jlSVMdf = optDf
locpos = .&((jlSVMdf[:m] .== 1.), 
            (jlSVMdf[:lambda] .== .2),
            (jlSVMdf[:kappa] .== minimum(jlSVMdf[:kappa])),
            (jlSVMdf[:sigmah] .== .35),) 
jlSVMdf[locpos, :]

In [ ]:
m_comb_num = 131
optDf[optDf[:m_comb_num] .== m_comb_num, :]
jlSlice = DataFrames.DataFrame(optDf[optDf[:m_comb_num] .== m_comb_num, :])

In [ ]:
cvmOptDF

In [ ]:
sbt, svm = Batch.get_bt_svm(;m=1., comb_num=m_comb_num,
                            display_msgs=true)

svm.c = jlSlice[1, :c]
svm.p = jlSlice[1, :p]
EqFinDiff.eq_fd(svm, jlSlice[1, :vb])

# TRASH